# Battle of the Neighborhoods
### My client is considering moving to a new city and wants help determining the right fit for her.  She does not want to own a car. With a list of the cities with the best public transportation and her input, the search was narrowed down to 5 major cities: San Francisco, Boston, Philadelphia, Chicago and Portland, OR. She currently lives in the East Village of NYC and enjoys the neighborhood emensely.  She would like to live in a similar neighborhood.  FourSquare data, along with a neighborhood list from each of the 5 cities will be used to determine which neighborhoods are similar to the East Village.

## Import Libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

# !conda install -c conda-forge geocoder --yes

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    altair-4.0.1               |             py_0         575 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge
    certifi-2019.11.28         |           py36_0         149 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    openssl-1.1.1d             |       h516909a_0         2.1 MB  conda-forge
    branca-0.3.1               |             py_0          25 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.0 MB

The following NEW packages will be 

## Data
### Import Neighborhood Locations

In [2]:
DF_NBR_LatLongs = pd.read_csv('https://raw.githubusercontent.com/adamson22/Coursera_Capstone/master/NeighborhoodLocations.csv',encoding = "ISO-8859-1") 
DF_NBR_LatLongs.head(10)

City     Neighborhood   Latitude  Longitude
0  Philadelphia   Allegheny West  40.008446 -75.177956
1  Philadelphia      Bella Vista  39.935391 -75.157122
2  Philadelphia       Bridesburg  40.000390 -75.069618
3  Philadelphia        Bustleton  40.082611 -75.031560
4  Philadelphia    Chestnut Hill  40.077055 -75.207400
5  Philadelphia      Cobbs Creek  39.947613 -75.240182
6  Philadelphia       East Falls  40.014557 -75.191568
7  Philadelphia  East Mount Airy  40.064500 -75.187500
8  Philadelphia    East Oak Lane  40.050111 -75.132953
9  Philadelphia         Eastwick  39.890391 -75.242405

## Look at maps and neighborhood list of each city's neighborhoods

In [3]:
address = 'Philadelphia, PA'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Philadelphia are {}, {}.'.format(latitude, longitude))
df_phili = DF_NBR_LatLongs[DF_NBR_LatLongs['City']=='Philadelphia']
print(df_phili.shape)
df_phili

The geograpical coordinate of Philadelphia are 39.9527237, -75.1635262.
(54, 4)


City             Neighborhood   Latitude  Longitude
0   Philadelphia           Allegheny West  40.008446 -75.177956
1   Philadelphia              Bella Vista  39.935391 -75.157122
2   Philadelphia               Bridesburg  40.000390 -75.069618
3   Philadelphia                Bustleton  40.082611 -75.031560
4   Philadelphia            Chestnut Hill  40.077055 -75.207400
5   Philadelphia              Cobbs Creek  39.947613 -75.240182
6   Philadelphia               East Falls  40.014557 -75.191568
7   Philadelphia          East Mount Airy  40.064500 -75.187500
8   Philadelphia            East Oak Lane  40.050111 -75.132953
9   Philadelphia                 Eastwick  39.890391 -75.242405
10  Philadelphia                Fairmount  39.972335 -75.181012
11  Philadelphia                Fox Chase  40.081222 -75.080173
12  Philadelphia                Frankford  40.028167 -75.084896
13  Philadelphia               Germantown  40.043445 -75.180177
14  Philadelphia              Grays Ferry  39.935113 -75.192124
15  Philadelphia               Holmesburg  40.041500 -75.027949
16  Philadelphia             Hunting Park  40.016501 -75.143788
17  Philadelphia                  Juniata  40.008446 -75.108786
18  Philadelphia               Kensington  39.985946 -75.131843
19  Philadelphia              Kingsessing  39.936780 -75.229626
20  Philadelphia                Lawncrest  40.046900 -75.096700
21  Philadelphia                    Logan  40.028445 -75.151565
22  Philadelphia                 Manayunk  40.024557 -75.214068
23  Philadelphia                   Mantua  39.962613 -75.191290
24  Philadelphia                  Mayfair  40.033723 -75.034060
25  Philadelphia            North Central  39.975113 -75.162956
26  Philadelphia       Northern Liberties  39.965946 -75.146288
27  Philadelphia                    Olney  40.041223 -75.123786
28  Philadelphia                Overbrook  39.989279 -75.243237
29  Philadelphia            Oxford Circle  40.050111 -75.071839
30  Philadelphia                 Parkside  39.978446 -75.220458
31  Philadelphia             Point Breeze  39.933446 -75.177956
32  Philadelphia            Port Richmond  39.976779 -75.100175
33  Philadelphia                 Powelton  39.958446 -75.191012
34  Philadelphia            Queen Village  39.934280 -75.148510
35  Philadelphia               Rhawnhurst  40.061778 -75.055728
36  Philadelphia               Roxborough  40.038167 -75.222402
37  Philadelphia               Schuylkill  39.942335 -75.187123
38  Philadelphia                 Somerton  40.123443 -75.014892
39  Philadelphia                  Stenton  39.989835 -75.159344
40  Philadelphia                   Tacony  40.031223 -75.044339
41  Philadelphia                    Tioga  40.009001 -75.167956
42  Philadelphia               Torresdale  40.054834 -75.004337
43  Philadelphia          University City  39.949279 -75.189624
44  Philadelphia          West Mount Airy  40.052611 -75.197956
45  Philadelphia            West Oak Lane  40.069278 -75.166287
46  Philadelphia               Wynnefield  39.989835 -75.237681
47  Philadelphia              Center City  39.952449 -75.166441
48  Philadelphia       South Philadelphia  39.921566 -75.175834
49  Philadelphia   Southwest Philadelphia  39.911786 -75.232644
50  Philadelphia  North Philadelphia West  39.984865 -75.171770
51  Philadelphia                 Fairhill  39.999283 -75.137589
52  Philadelphia          East Germantown  40.044825 -75.168452
53  Philadelphia   Northeast Philadelphia  40.050674 -75.066800

In [4]:
# create map of Philadelphia using latitude and longitude values
map_phili = folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map
for lat, lng, neighborhood in zip(df_phili['Latitude'], df_phili['Longitude'],  df_phili['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_phili)  
    
map_phili

In [5]:
address = 'Boston, MA'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Boston are {}, {}.'.format(latitude, longitude))
df_boston = DF_NBR_LatLongs[DF_NBR_LatLongs['City']=='Boston']
print(df_boston.shape)
df_boston

The geograpical coordinate of Boston are 42.3602534, -71.0582912.
(22, 4)


City    Neighborhood   Latitude  Longitude
142  Boston         Allston  42.359489 -71.142382
143  Boston        Back Bay  42.350097 -71.086996
144  Boston     Bay Village  42.350653 -71.069773
145  Boston     Beacon Hill  42.358708 -71.067829
146  Boston        Brighton  42.350097 -71.156442
147  Boston     Charlestown  42.377875 -71.061996
148  Boston       Chinatown  42.349814 -71.068382
149  Boston      Dorchester  42.297321 -71.074495
150  Boston        Downtown  42.354542 -71.057829
151  Boston     East Boston  42.375097 -71.039217
152  Boston  Fenway Kenmore  42.342586 -71.114255
153  Boston       Hyde Park  42.255654 -71.124496
154  Boston   Jamaica Plain  42.309820 -71.120330
155  Boston        Mattapan  42.272321 -71.086995
156  Boston    Mission Hill  42.331314 -71.110802
157  Boston       North End  42.365097 -71.054495
158  Boston      Roslindale  42.291209 -71.124497
159  Boston         Roxbury  42.325098 -71.095329
160  Boston    South Boston  42.333431 -71.049495
161  Boston       South End  42.339443 -71.084551
162  Boston        West End  42.364746 -71.070421
163  Boston    West Roxbury  42.279265 -71.149497

In [6]:
# create map of Boston using latitude and longitude values
map_boston = folium.Map(location=[latitude, longitude], zoom_start=13)

# add markers to map
for lat, lng, neighborhood in zip(df_boston['Latitude'], df_boston['Longitude'],  df_boston['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_boston)  
    
map_boston

In [8]:
address = 'Chicago, IL'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Chicago are {}, {}.'.format(latitude, longitude))
df_chicago = DF_NBR_LatLongs[DF_NBR_LatLongs['City']=='Chicago']
print(df_chicago.shape)
df_chicago

The geograpical coordinate of Chicago are 41.8755616, -87.6244212.
(75, 4)


City            Neighborhood   Latitude  Longitude
164  Chicago             Albany Park  41.968365 -87.723392
165  Chicago          Archer Heights  41.811422 -87.726165
166  Chicago           Armour Square  41.840033 -87.633107
167  Chicago                 Ashburn  41.747533 -87.711163
168  Chicago          Auburn Gresham  41.743388 -87.673671
169  Chicago                  Austin  41.887532 -87.764780
170  Chicago             Avalon Park  41.745035 -87.588658
171  Chicago                Avondale  41.938921 -87.711168
172  Chicago          Belmont Cragin  41.931698 -87.768670
173  Chicago                 Beverly  41.718089 -87.673661
174  Chicago              Bridgeport  41.838089 -87.651163
175  Chicago           Brighton Park  41.818922 -87.698942
176  Chicago                Burnside  41.729419 -87.604366
177  Chicago         Calumet Heights  41.730035 -87.579213
178  Chicago                 Chatham  41.741145 -87.612548
179  Chicago            Chicago Lawn  41.775033 -87.696441
180  Chicago                Clearing  41.778088 -87.761721
181  Chicago                 Douglas  41.834756 -87.618106
182  Chicago                 Dunning  41.952809 -87.796449
183  Chicago      East Garfield Park  41.880866 -87.702833
184  Chicago               East Side  41.712257 -87.531989
185  Chicago               Edgewater  41.983365 -87.663945
186  Chicago             Edison Park  41.998642 -87.823952
187  Chicago               Englewood  41.779756 -87.645884
188  Chicago             Forest Glen  41.991701 -87.793395
189  Chicago             Fuller Park  41.818089 -87.632551
190  Chicago               Gage Park  41.795033 -87.696164
191  Chicago          Garfield Ridge  41.803398 -87.804705
192  Chicago         Grand Boulevard  41.813923 -87.617272
193  Chicago  Greater Grand Crossing  41.755590 -87.600326
194  Chicago               Hegewisch  41.653646 -87.546988
195  Chicago                 Hermosa  41.928643 -87.734502
196  Chicago           Humboldt Park  41.902810 -87.720890
197  Chicago               Hyde Park  41.794201 -87.593938
198  Chicago             Irving Park  41.953365 -87.736447
199  Chicago          Jefferson Park  41.970587 -87.763393
200  Chicago                 Kenwood  41.809201 -87.597549
201  Chicago            Lincoln Park  41.921699 -87.647832
202  Chicago          Lincoln Square  41.975865 -87.689224
203  Chicago            Logan Square  41.923365 -87.699223
204  Chicago         Lower West Side  41.854200 -87.665609
205  Chicago           McKinley Park  41.831700 -87.673664
206  Chicago               Montclare  41.927878 -87.815590
207  Chicago             Morgan Park  41.690312 -87.666716
208  Chicago         Mount Greenwood  41.698089 -87.708662
209  Chicago         Near North Side  41.900033 -87.634497
210  Chicago         Near South Side  41.856700 -87.624774
211  Chicago          Near West Side  41.880033 -87.666720
212  Chicago                New City  41.807533 -87.656440
213  Chicago            North Center  41.953921 -87.678945
214  Chicago          North Lawndale  41.860032 -87.718388
215  Chicago              North Park  41.980587 -87.720892
216  Chicago            Norwood Park  41.985619 -87.824735
217  Chicago                 Oakland  41.823089 -87.603939
218  Chicago            Portage Park  41.957809 -87.765059
219  Chicago                 Pullman  41.957809 -87.765059
220  Chicago               Riverdale  41.957809 -87.765059
221  Chicago             Rogers Park  42.008643 -87.666724
222  Chicago                Roseland  41.701979 -87.625881
223  Chicago           South Chicago  41.722813 -87.536434
224  Chicago           South Deering  41.692257 -87.558379
225  Chicago          South Lawndale  41.843644 -87.712554
226  Chicago             South Shore  41.761979 -87.577825
227  Chicago                The Loop  41.878971 -87.637882
228  Chicago                  Uptown  41.981699 -87.659778
229  Chicago      Washington Heights  41.706423 -87.656160
230  Chicago         Washington Park  41.792534 -87.618

In [9]:
# create map of Chicago using latitude and longitude values
map_chicago = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(df_chicago['Latitude'], df_chicago['Longitude'],  df_chicago['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_chicago)  
    
map_chicago

In [10]:
address = 'San Francisco, CA, USA'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of San Francisco are {}, {}.'.format(latitude, longitude))
df_sf = DF_NBR_LatLongs[DF_NBR_LatLongs['City']== 'San Francisco']
print(df_sf.shape)
df_sf

The geograpical coordinate of San Francisco are 37.7790262, -122.4199061.
(88, 4)


City           Neighborhood   Latitude   Longitude
54   San Francisco           Alamo Square  37.777745 -122.437731
55   San Francisco             Anza Vista  37.781004 -122.444436
56   San Francisco        Ashbury Heights  37.762847 -122.451533
57   San Francisco         Balboa Terrace  37.730898 -122.470185
58   San Francisco                Bayview  37.734097 -122.391360
59   San Francisco         Bernal Heights  37.739540 -122.418049
60   San Francisco                 Castro  37.762771 -122.439926
61   San Francisco         Cathedral Hill  37.784344 -122.426738
62   San Francisco            China Basin  37.779502 -122.394993
63   San Francisco              Chinatown  37.796596 -122.408582
64   San Francisco           Civic Center  37.778972 -122.420653
65   San Francisco      Clarendon Heights  37.755155 -122.454725
66   San Francisco            Cole Valley  37.764859 -122.458546
67   San Francisco         Corona Heights  37.761391 -122.446164
68   San Francisco         Crocker Amazon  37.712232 -122.447553
69   San Francisco        Design District  37.768924 -122.403910
70   San Francisco        Diamond Heights  37.745764 -122.441638
71   San Francisco        Dolores Heights  37.756947 -122.437816
72   San Francisco        Duboce Triangle  37.766159 -122.435493
73   San Francisco          Eureka Valley  37.760931 -122.448007
74   San Francisco              Excelsior  37.724133 -122.438455
75   San Francisco               Fillmore  37.780811 -122.438462
76   San Francisco     Financial District  37.792773 -122.409847
77   San Francisco       Fishermans Wharf  37.808110 -122.425386
78   San Francisco            Forest Hill  37.747431 -122.463583
79   San Francisco          Forest Knolls  37.754444 -122.459167
80   San Francisco              Glen Park  37.737910 -122.436481
81   San Francisco    Golden Gate Heights  37.754722 -122.471111
82   San Francisco         Haight Ashbury  37.769930 -122.446916
83   San Francisco           Hayes Valley  37.774713 -122.429710
84   San Francisco          Hunters Point  37.730311 -122.417540
85   San Francisco              Ingleside  37.722987 -122.453027
86   San Francisco     Ingleside Terraces  37.724167 -122.466389
87   San Francisco           Inner Sunset  37.757526 -122.473058
88   San Francisco           Islais Creek  37.746552 -122.394115
89   San Francisco            Jordan Park  37.783794 -122.460746
90   San Francisco               Lakeside  37.725884 -122.482213
91   San Francisco              Lakeshore  37.719337 -122.507118
92   San Francisco         Laurel Heights  37.784418 -122.454827
93   San Francisco       Little Hollywood  37.711963 -122.402699
94   San Francisco          Little Russia  37.780238 -122.485924
95   San Francisco          Lone Mountain  37.778345 -122.457045
96   San Francisco           Lower Haight  37.771721 -122.438088
97   San Francisco  Lower Pacific Heights  37.786292 -122.444531
98   San Francisco         Lower Nob Hill  37.789084 -122.418035
99   San Francisco        Marina District  37.803835 -122.446229
100  San Francisco         Merced Heights  37.718611 -122.468056
101  San Francisco           Merced Manor  37.733333 -122.477222
102  San Francisco        Midtown Terrace  37.751143 -122.461975
103  San Francisco             Mid Market  37.780153 -122.415837
104  San Francisco            Mission Bay  37.771456 -122.399293
105  San Francisco       Mission District  37.759930 -122.419138
106  San Francisco        Mission Terrace  37.724358 -122.446749
107  San Francisco       Monterey Heights  37.733207 -122.471214
108  San Francisco         Mount Davidson  37.738332 -122.462088
109  San Francisco               Nob Hill  37.792944 -122.420489
110  San Francisco             Noe Valley  37.749055 -122.443232
111  San Francisco            North Beach  37.805762 -122.412193
112  San Francisco     North of Panhandle  37.776317 -122.446729
113  San Francisco              Oceanview  37.709376 -122.438583
114  San Francisco           Outer Sunset  37.755

In [11]:
# create map of SF using latitude and longitude values
map_sf = folium.Map(location=[latitude, longitude], zoom_start=13)

# add markers to map
for lat, lng, neighborhood in zip(df_sf['Latitude'], df_sf['Longitude'],  df_sf['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_sf)  
    
map_sf

In [12]:
address = 'Portland, OR'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Portland are {}, {}.'.format(latitude, longitude))
df_portland = DF_NBR_LatLongs[DF_NBR_LatLongs['City']=='Portland OR']
print(df_portland.shape)
df_portland

The geograpical coordinate of Portland are 45.5202471, -122.6741949.
(94, 4)


City             Neighborhood   Latitude   Longitude
239  Portland OR                  Alameda  45.555118 -122.630651
240  Portland OR              Arbor Lodge  45.571769 -122.702022
241  Portland OR  Ardenwald Johnson Creek  45.454265 -122.645134
242  Portland OR                    Argay  45.556535 -122.541469
243  Portland OR        Arlington Heights  45.519320 -122.718405
244  Portland OR             Arnold Creek  45.441109 -122.715684
245  Portland OR                 Ashcreek  45.453996 -122.755545
246  Portland OR        Beaumont Wilshire  45.549939 -122.640274
247  Portland OR                    Boise  45.549109 -122.678953
248  Portland OR     Brentwood Darlington  45.468550 -122.615269
249  Portland OR                Bridgeton  45.603429 -122.677551
250  Portland OR               Bridlemile  45.493174 -122.710374
251  Portland OR                 Brooklyn  45.490397 -122.637317
252  Portland OR                  Buckman  45.517564 -122.661919
253  Portland OR           Cathedral Park  45.587691 -122.774349
254  Portland OR               Centennial  45.505625 -122.516147
255  Portland OR             Collins View  45.453086 -122.695412
256  Portland OR                Concordia  45.566009 -122.649712
257  Portland OR       Creston Kenilworth  45.494136 -122.637626
258  Portland OR                Crestwood  45.453984 -122.736700
259  Portland OR                    Cully  45.563618 -122.616589
260  Portland OR            East Columbia  45.594014 -122.663933
261  Portland OR             Eastmoreland  45.473175 -122.624261
262  Portland OR                    Eliot  45.540091 -122.688258
263  Portland OR            Far Southwest  45.439666 -122.743891
264  Portland OR            Foster Powell  45.490211 -122.603971
265  Portland OR                 Glenfair  45.522816 -122.508217
266  Portland OR             Goose Hollow  45.518524 -122.702318
267  Portland OR               Grant Park  45.539413 -122.635797
268  Portland OR            Hayden Island  45.625264 -122.717850
269  Portland OR                 Hayhurst  45.481669 -122.745128
270  Portland OR                Hazelwood  45.516509 -122.523981
271  Portland OR            Healy Heights  45.492661 -122.704384
272  Portland OR                Hillsdale  45.481507 -122.694818
273  Portland OR                 Hillside  45.526013 -122.722251
274  Portland OR                Hollywood  45.534669 -122.628916
275  Portland OR                Homestead  45.495788 -122.705161
276  Portland OR        Hosford Abernethy  45.505286 -122.670658
277  Portland OR                 Humboldt  45.560528 -122.680381
278  Portland OR                Irvington  45.540396 -122.652040
279  Portland OR                   Kenton  45.581784 -122.681486
280  Portland OR                    Kerns  45.526932 -122.667474
281  Portland OR                     King  45.557369 -122.675249
282  Portland OR              Laurelhurst  45.526986 -122.633448
283  Portland OR                    Lents  45.477397 -122.598353
284  Portland OR                  Linnton  45.526230 -122.622873
285  Portland OR         Lloyd DistrictÂ   45.530176 -122.671065
286  Portland OR            Madison South  45.542603 -122.594795
287  Portland OR                Maplewood  45.469841 -122.730097
288  Portland OR                  Markham  45.456307 -122.710068
289  Portland OR            Marshall Park  45.454526 -122.711182
290  Portland OR                Mill Park  45.511578 -122.552946
291  Portland OR               Montavilla  45.519008 -122.578982
292  Portland OR         Mt. Scott Arleta  45.483667 -122.599345
293  Portland OR                Mt. Tabor  45.514292 -122.616607
294  Portland OR                Multnomah  45.469563 -122.707318
295  Portland OR              North Tabor  45.526600 -122.613597
296  Portland OR       Northwest District  45.567824 -122.822291
297  Portland OR        Northwest Heights  45.541204 -122.787354
298  Portland OR     Northwest Industrial  45.561110 -122.764053
299  Portland OR       Old Town Chinatown  45.5

In [13]:
# create map of Portland using latitude and longitude values
map_portland = folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map
for lat, lng, neighborhood in zip(df_portland['Latitude'], df_portland['Longitude'],  df_portland['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_portland)  
    
map_portland

## Get FourSquare Data - Venues in each neighborhood

In [14]:
CLIENT_ID = 'XXXX' # your Foursquare ID
CLIENT_SECRET = 'XXXX' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 150 # number of returns

In [15]:
# Setup function to make FourSquare calls
# retrieves all venues within 500m of give lat,longs
def getNearbyVenues(cities, names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for city, name, lat, lng in zip(cities, names, latitudes, longitudes):
        print(name + ' in ' + city)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']

        # return only relevant information for each nearby venue
        venues_list.append([(
            city,
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['City','Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [16]:
# Call function for each neighborhood.
all_venues = getNearbyVenues(cities=DF_NBR_LatLongs['City'],
                            names=DF_NBR_LatLongs['Neighborhood'],
                            latitudes=DF_NBR_LatLongs['Latitude'],
                            longitudes=DF_NBR_LatLongs['Longitude'])

Allegheny West in Philadelphia
Bella Vista in Philadelphia
Bridesburg in Philadelphia
Bustleton in Philadelphia
Chestnut Hill in Philadelphia
Cobbs Creek in Philadelphia
East Falls in Philadelphia
East Mount Airy in Philadelphia
East Oak Lane in Philadelphia
Eastwick in Philadelphia
Fairmount in Philadelphia
Fox Chase in Philadelphia
Frankford in Philadelphia
Germantown in Philadelphia
Grays Ferry in Philadelphia
Holmesburg in Philadelphia
Hunting Park in Philadelphia
Juniata in Philadelphia
Kensington in Philadelphia
Kingsessing in Philadelphia
Lawncrest in Philadelphia
Logan in Philadelphia
Manayunk in Philadelphia
Mantua in Philadelphia
Mayfair in Philadelphia
North Central in Philadelphia
Northern Liberties in Philadelphia
Olney in Philadelphia
Overbrook in Philadelphia
Oxford Circle in Philadelphia
Parkside in Philadelphia
Point Breeze in Philadelphia
Port Richmond in Philadelphia
Powelton in Philadelphia
Queen Village in Philadelphia
Rhawnhurst in Philadelphia
Roxborough in Phila

#### Look at the table created from pulling all the venues.  8,583 records and looks good.

In [17]:
print(all_venues.shape)
all_venues.head(10)

(8583, 8)


City    Neighborhood  Neighborhood Latitude  \
0  Philadelphia  Allegheny West              40.008446   
1  Philadelphia  Allegheny West              40.008446   
2  Philadelphia  Allegheny West              40.008446   
3  Philadelphia  Allegheny West              40.008446   
4  Philadelphia  Allegheny West              40.008446   
5  Philadelphia  Allegheny West              40.008446   
6  Philadelphia  Allegheny West              40.008446   
7  Philadelphia  Allegheny West              40.008446   
8  Philadelphia  Allegheny West              40.008446   
9  Philadelphia  Allegheny West              40.008446   

   Neighborhood Longitude                   Venue  Venue Latitude  \
0              -75.177956          Planet Fitness       40.008568   
1              -75.177956       PA Wine & Spirits       40.009335   
2              -75.177956                ShopRite       40.009783   
3              -75.177956      SHARE Food Program       40.006208   
4              -75.177956        Restaurant Depot       40.009997   
5              -75.177956  Philadelphia Rock Gyms       40.008428   
6              -75.177956                 Dunkin'       40.007603   
7              -75.177956                Wingstop       40.010768   
8              -75.177956           Bakers Square       40.009786   
9              -75.177956                  Subway       40.010724   

   Venue Longitude        Venue Category  
0       -75.176718  Gym / Fitness Center  
1       -75.175383          Liquor Store  
2       -75.174842         Grocery Store  
3       -75.177470         Grocery Store  
4       -75.177746  Kitchen Supply Store  
5       -75.183449          Climbing Gym  
6       -75.174371            Donut Shop  
7       -75.177072           Wings Joint  
8       -75.174875        Shopping Plaza  
9       -75.176284        Sandwich Place

#### Look at how many venues were pulled for New York neighborhood (East Village).  100 Venues looks good.

In [18]:
all_venues[all_venues['City']=='New York'].shape

(100, 8)

## My client is looking for neighborhoods similar to the East Village so remove venue categories not in EV.
#### First lets look at what venues are in the EV. 57 venues look good.

In [19]:
NYC_Venue_list = all_venues[all_venues['City']=='New York']['Venue Category'].unique().tolist()
NYC_Venue_list

['Beer Store',
 'Moroccan Restaurant',
 'Pet Café',
 'Japanese Restaurant',
 'Dog Run',
 'Scandinavian Restaurant',
 'Korean Restaurant',
 'Wine Bar',
 'Bagel Shop',
 'American Restaurant',
 'Hot Dog Joint',
 'Coffee Shop',
 'Pizza Place',
 'Dessert Shop',
 'Cheese Shop',
 'Ice Cream Shop',
 'Park',
 'Vietnamese Restaurant',
 'Bar',
 'Caribbean Restaurant',
 'Juice Bar',
 'Hobby Shop',
 'Gift Shop',
 'Swiss Restaurant',
 'Vegetarian / Vegan Restaurant',
 'Speakeasy',
 'Wine Shop',
 'Greek Restaurant',
 'Gourmet Shop',
 'Burger Joint',
 'Bakery',
 'Ramen Restaurant',
 'Seafood Restaurant',
 'Spa',
 'Taiwanese Restaurant',
 'Beer Bar',
 'Middle Eastern Restaurant',
 'Tapas Restaurant',
 'Mexican Restaurant',
 'Cocktail Bar',
 'Organic Grocery',
 'Italian Restaurant',
 'Chinese Restaurant',
 'Cupcake Shop',
 'Filipino Restaurant',
 'Garden Center',
 'Used Bookstore',
 'Soup Place',
 'Pilates Studio',
 'Record Shop',
 'Farmers Market',
 'Art Gallery',
 'Argentinian Restaurant',
 'Arepa Res

#### Pull only venues that match venue categories in EV.

In [20]:
all_cities_NYCV = all_venues[all_venues['Venue Category'].isin(NYC_Venue_list)]
all_cities_NYCV

City             Neighborhood  Neighborhood Latitude  \
11     Philadelphia           Allegheny West              40.008446   
27     Philadelphia           Allegheny West              40.008446   
30     Philadelphia              Bella Vista              39.935391   
31     Philadelphia              Bella Vista              39.935391   
32     Philadelphia              Bella Vista              39.935391   
34     Philadelphia              Bella Vista              39.935391   
36     Philadelphia              Bella Vista              39.935391   
37     Philadelphia              Bella Vista              39.935391   
39     Philadelphia              Bella Vista              39.935391   
41     Philadelphia              Bella Vista              39.935391   
42     Philadelphia              Bella Vista              39.935391   
43     Philadelphia              Bella Vista              39.935391   
44     Philadelphia              Bella Vista              39.935391   
46     Philadelphia              Bella Vista              39.935391   
47     Philadelphia              Bella Vista              39.935391   
48     Philadelphia              Bella Vista              39.935391   
49     Philadelphia              Bella Vista              39.935391   
51     Philadelphia              Bella Vista              39.935391   
53     Philadelphia              Bella Vista              39.935391   
54     Philadelphia              Bella Vista              39.935391   
57     Philadelphia              Bella Vista              39.935391   
58     Philadelphia              Bella Vista              39.935391   
59     Philadelphia              Bella Vista              39.935391   
61     Philadelphia              Bella Vista              39.935391   
62     Philadelphia              Bella Vista              39.935391   
63     Philadelphia              Bella Vista              39.935391   
64     Philadelphia              Bella Vista              39.935391   
68     Philadelphia              Bella Vista              39.935391   
69     Philadelphia              Bella Vista              39.935391   
70     Philadelphia              Bella Vista              39.935391   
71     Philadelphia              Bella Vista              39.935391   
72     Philadelphia              Bella Vista              39.935391   
74     Philadelphia              Bella Vista              39.935391   
75     Philadelphia              Bella Vista              39.935391   
76     Philadelphia              Bella Vista              39.935391   
78     Philadelphia              Bella Vista              39.935391   
80     Philadelphia              Bella Vista              39.935391   
83     Philadelphia              Bella Vista              39.935391   
84     Philadelphia              Bella Vista              39.935391   
87     Philadelphia               Bridesburg              40.000390   
91     Philadelphia               Bridesburg              40.000390   
93     Philadelphia               Bridesburg              40.000390   
95     Philadelphia               Bridesburg              40.000390   
100    Philadelphia                Bustleton              40.082611   
102    Philadelphia                Bustleton              40.082611   
109    Philadelphia                Bustleton              40.082611   
113    Philadelphia                Bustleton              40.082611   
114    Philadelphia                Bustleton              40.082611   
116    Philadelphia            Chestnut Hill              40.077055   
118    Philadelphia            Chestnut Hill              40.077055   
120    Philadelphia            Chestnut Hill              40.077055   
121    Philadelphia            Chestnut Hill              40.077055   
122    Philadelphia            Chestnut Hill              40.077055   
123    Philadelphia            Chestnut Hill              40.077055   
124    Philadelphia            Chestnut Hill              40.077055   
125    Philadelphia            Chestnut

#### Look at number of NYC venues categories and combare to categories in new restricted table.  Both 57. Good. Look at category list in new restricted table.

In [41]:
print(len(NYC_Venue_list))
print(all_cities_NYCV.groupby(['Venue Category']).count().shape)
all_cities_NYCV.groupby(['Venue Category']).count()

57
(57, 7)


City  Neighborhood  Neighborhood Latitude  \
Venue Category                                                             
American Restaurant             150           150                    150   
Arepa Restaurant                  1             1                      1   
Argentinian Restaurant            7             7                      7   
Art Gallery                      59            59                     59   
Arts & Crafts Store              37            37                     37   
Bagel Shop                       12            12                     12   
Bakery                          143           143                    143   
Bar                             193           193                    193   
Beer Bar                         25            25                     25   
Beer Store                       14            14                     14   
Burger Joint                     66            66                     66   
Caribbean Restaurant             10            10                     10   
Cheese Shop                       7             7                      7   
Chinese Restaurant              125           125                    125   
Cocktail Bar                     82            82                     82   
Coffee Shop                     346           346                    346   
Cupcake Shop                      6             6                      6   
Dessert Shop                     43            43                     43   
Dog Run                          40            40                     40   
Farmers Market                   23            23                     23   
Filipino Restaurant               8             8                      8   
Flower Shop                      22            22                     22   
French Restaurant                42            42                     42   
Garden Center                     6             6                      6   
Gift Shop                        41            41                     41   
Gourmet Shop                     23            23                     23   
Greek Restaurant                 13            13                     13   
Hobby Shop                        7             7                      7   
Hot Dog Joint                    16            16                     16   
Ice Cream Shop                   81            81                     81   
Italian Restaurant              172           172                    172   
Japanese Restaurant              49            49                     49   
Juice Bar                        35            35                     35   
Korean Restaurant                42            42                     42   
Mexican Restaurant              182           182                    182   
Middle Eastern Restaurant        21            21                     21   
Moroccan Restaurant               8             8                      8   
Organic Grocery                   3             3                      3   
Park                            229           229                    229   
Pet Café                          1             1                      1   
Pilates Studio                    9             9                      9   
Pizza Place                     258           258                    258   
Ramen Restaurant                 18            18                     18   
Record Shop                      20            20                     20   
Scandinavian Restaurant           5             5                      5   
Seafood Restaurant               74            74                     74   
Soup Place                        2             2                      2   
Spa                              59            59                     59   
Speakeasy                        18            18                     18   
Swiss Restaurant                  2             2                      2   
Taiwanese Restaurant              3             3                      3   
Tap

## Some neighborhoods have very few venues. Research to see what is enough to consider.
#### Look at how many venues per neighborhood.

In [21]:
NBR_check =all_cities_NYCV.groupby(['City','Neighborhood']).count()
print(NBR_check.shape)
NBR_check

(298, 6)


Neighborhood Latitude  \
City          Neighborhood                                     
Boston        Allston                                      8   
              Back Bay                                    36   
              Bay Village                                 37   
              Beacon Hill                                 23   
              Brighton                                    15   
              Charlestown                                 10   
              Chinatown                                   34   
              Dorchester                                   2   
              Downtown                                    34   
              East Boston                                 12   
              Fenway Kenmore                               5   
              Hyde Park                                    8   
              Jamaica Plain                                9   
              Mission Hill                                 3   
              North End                                   64   
              Roslindale                                   2   
              Roxbury                                      2   
              South Boston                                21   
              South End                                   24   
              West End                                    16   
Chicago       Albany Park                                  8   
              Archer Heights                               7   
              Armour Square                                6   
              Ashburn                                      1   
              Auburn Gresham                               2   
              Austin                                       3   
              Avalon Park                                  3   
              Avondale                                     7   
              Belmont Cragin                               5   
              Beverly                                      5   
              Bridgeport                                  17   
              Brighton Park                                8   
              Burnside                                     1   
              Calumet Heights                              1   
              Chatham                                      1   
              Chicago Lawn                                 7   
              Clearing                                     3   
              Douglas                                      7   
              Dunning                                      1   
              East Garfield Park                           2   
              East Side                                    4   
              Edgewater                                   13   
              Edison Park                                  2   
              Englewood                                    3   
              Forest Glen                                  8   
              Fuller Park                                  1   
              Gage Park                                    4   
              Grand Boulevard                              5   
              Greater Grand Crossing                       2   
              Hegewisch                                    5   
              Hermosa                                      4   
              Humboldt Park                                1   
              Hyde Park                                   10   
              Irving Park                                  9   
              Jefferson Park                              11   
              Kenwood                                      5   
              Lincoln Park                                35   
              Lincoln Square                              14   
              Logan Square                                30   
              Lower West Side                             25   
              McKinley Park                                6   
       

#### Study neighborhoods with less than 5 venues. Are they areas to consider?  With so few venues may not be worth including.

In [22]:
print(NBR_check[NBR_check['Venue']<5].shape)
NBR_check[NBR_check['Venue']<5]

(125, 6)


Neighborhood Latitude  \
City          Neighborhood                                     
Boston        Dorchester                                   2   
              Mission Hill                                 3   
              Roslindale                                   2   
              Roxbury                                      2   
Chicago       Ashburn                                      1   
              Auburn Gresham                               2   
              Austin                                       3   
              Avalon Park                                  3   
              Burnside                                     1   
              Calumet Heights                              1   
              Chatham                                      1   
              Clearing                                     3   
              Dunning                                      1   
              East Garfield Park                           2   
              East Side                                    4   
              Edison Park                                  2   
              Englewood                                    3   
              Fuller Park                                  1   
              Gage Park                                    4   
              Greater Grand Crossing                       2   
              Hermosa                                      4   
              Humboldt Park                                1   
              Mount Greenwood                              1   
              New City                                     4   
              North Park                                   1   
              Oakland                                      1   
              Roseland                                     1   
              South Chicago                                3   
              Washington Heights                           3   
              Washington Park                              1   
              West Elsdon                                  3   
              West Englewood                               1   
              West Lawn                                    4   
              West Pullman                                 2   
              West Ridge                                   4   
              Woodlawn                                     2   
Philadelphia  Allegheny West                               2   
              Bridesburg                                   4   
              Cobbs Creek                                  4   
              East Falls                                   3   
              East Germantown                              3   
              East Mount Airy                              1   
              Eastwick                                     2   
              Fairhill                                     4   
              Germantown                                   2   
              Grays Ferry                                  3   
              Juniata                                      1   
              Kensington                                   4   
              Kingsessing                                  4   
              Lawncrest                                    3   
              Mayfair                                      2   
              North Central                                4   
              North Philadelphia West                      1   
              Overbrook                                    1   
              Oxford Circle                                3   
              Parkside                                     2   
              Port Richmond                                1   
              Rhawnhurst                                   3   
              Schuylkill                                   4   
              Southwest Philadelphia                       1   
              Torresdale                                   2   
       

#### How many neighborhoods per city have less than 5 venues? Don't want to take too many neighborhoods away.  Will this leave enough neighborhoods to study?

In [23]:

NBR_check[NBR_check['Venue']<5].groupby('City').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
City                                                                  
Boston                             4                       4      4   
Chicago                           32                      32     32   
Philadelphia                      27                      27     27   
Portland OR                       44                      44     44   
San Francisco                     18                      18     18   

               Venue Latitude  Venue Longitude  Venue Category  
City                                                            
Boston                      4                4               4  
Chicago                    32               32              32  
Philadelphia               27               27              27  
Portland OR                44               44              44  
San Francisco              18               18              18

#### How many neighborhoods were there orignally by city? If we removed the neighborhoods with less than 5, what would that look like?  There are enough neighborhoods to remove.

In [24]:
all_cities_NYCV[['City','Neighborhood']].groupby('City').Neighborhood.nunique()

City
Boston           20
Chicago          69
New York          1
Philadelphia     50
Portland OR      77
San Francisco    81
Name: Neighborhood, dtype: int64

#### Research a few neighborhoods with low venue counts - Decided to remove anything less than 5 venues.

In [25]:
all_cities_NYCV[all_cities_NYCV['Neighborhood']=='Roxbury']
all_cities_NYCV[all_cities_NYCV['Neighborhood']=='Dorchester']

City Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
4972  Boston   Dorchester              42.297321              -71.074495   
4973  Boston   Dorchester              42.297321              -71.074495   

                          Venue  Venue Latitude  Venue Longitude  \
4972         Four Corners Pizza       42.299380       -71.073196   
4973  Oasis Vegan Veggie Parlor       42.299572       -71.073652   

                     Venue Category  
4972                    Pizza Place  
4973  Vegetarian / Vegan Restaurant

#### Remove neighborhoods with less than 5 venues

In [26]:
all_cities_NYCV_cut = pd.merge(NBR_check[NBR_check['Venue']>=5], all_cities_NYCV, how='inner', on=['City','Neighborhood'], left_on=None, right_on=None,
         left_index=False, right_index=False, sort=True,
         suffixes=('_x', '_y'), copy=True, indicator=False,
         validate=None)
all_cities_NYCV_cut.drop(['Neighborhood Latitude_x', 'Neighborhood Longitude_x', 'Venue_x','Venue Latitude_x', 'Venue Longitude_x', 'Venue Category_x'], axis=1,inplace=True)
col=list(all_venues.columns) 
print(col)
all_cities_NYCV_cut.columns = col
all_cities_NYCV_cut

['City', 'Neighborhood', 'Neighborhood Latitude', 'Neighborhood Longitude', 'Venue', 'Venue Latitude', 'Venue Longitude', 'Venue Category']


City            Neighborhood  Neighborhood Latitude  \
0            Boston                 Allston              42.359489   
1            Boston                 Allston              42.359489   
2            Boston                 Allston              42.359489   
3            Boston                 Allston              42.359489   
4            Boston                 Allston              42.359489   
5            Boston                 Allston              42.359489   
6            Boston                 Allston              42.359489   
7            Boston                 Allston              42.359489   
8            Boston                Back Bay              42.350097   
9            Boston                Back Bay              42.350097   
10           Boston                Back Bay              42.350097   
11           Boston                Back Bay              42.350097   
12           Boston                Back Bay              42.350097   
13           Boston                Back Bay              42.350097   
14           Boston                Back Bay              42.350097   
15           Boston                Back Bay              42.350097   
16           Boston                Back Bay              42.350097   
17           Boston                Back Bay              42.350097   
18           Boston                Back Bay              42.350097   
19           Boston                Back Bay              42.350097   
20           Boston                Back Bay              42.350097   
21           Boston                Back Bay              42.350097   
22           Boston                Back Bay              42.350097   
23           Boston                Back Bay              42.350097   
24           Boston                Back Bay              42.350097   
25           Boston                Back Bay              42.350097   
26           Boston                Back Bay              42.350097   
27           Boston                Back Bay              42.350097   
28           Boston                Back Bay              42.350097   
29           Boston                Back Bay              42.350097   
30           Boston                Back Bay              42.350097   
31           Boston                Back Bay              42.350097   
32           Boston                Back Bay              42.350097   
33           Boston                Back Bay              42.350097   
34           Boston                Back Bay              42.350097   
35           Boston                Back Bay              42.350097   
36           Boston                Back Bay              42.350097   
37           Boston                Back Bay              42.350097   
38           Boston                Back Bay              42.350097   
39           Boston                Back Bay              42.350097   
40           Boston                Back Bay              42.350097   
41           Boston                Back Bay              42.350097   
42           Boston                Back Bay              42.350097   
43           Boston                Back Bay              42.350097   
44           Boston             Bay Village              42.350653   
45           Boston             Bay Village              42.350653   
46           Boston             Bay Village              42.350653   
47           Boston             Bay Village              42.350653   
48           Boston             Bay Village              42.350653   
49           Boston             Bay Village              42.350653   
50           Boston             Bay Village              42.350653   
51           Boston             Bay Village              42.350653   
52           Boston             Bay Village              42.350653   
53           Boston             Bay Village              42.350653   
54           Boston             Bay Village              42.350653   
55           Boston             Bay Village              42.350653   
56           Boston      

## Create a dataset that shows, for each neighborhood, the number of venues by category.
#### For each category, put the percent of the venues that fall in that category.

In [27]:
# one hot encoding
city5_cut_onehot = pd.get_dummies(all_cities_NYCV_cut[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
city5_cut_onehot['Neighborhood'] = all_cities_NYCV_cut['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [city5_cut_onehot.columns[-1]] + list(city5_cut_onehot.columns[:-1])
city5_cut_onehot = city5_cut_onehot[fixed_columns]


# add neighborhood column back to dataframe
city5_cut_onehot['City'] = all_cities_NYCV_cut['City'] 

# move neighborhood column to the first column
fixed_columns = [city5_cut_onehot.columns[-1]] + list(city5_cut_onehot.columns[:-1])
city5_cut_onehot = city5_cut_onehot[fixed_columns]
city5_cut_onehot

city5_cut_grouped = city5_cut_onehot.groupby(['City','Neighborhood']).mean().reset_index()
print(city5_cut_grouped.shape)
city5_cut_grouped

(173, 59)


City            Neighborhood  American Restaurant  \
0           Boston                 Allston             0.125000   
1           Boston                Back Bay             0.111111   
2           Boston             Bay Village             0.108108   
3           Boston             Beacon Hill             0.130435   
4           Boston                Brighton             0.066667   
5           Boston             Charlestown             0.000000   
6           Boston               Chinatown             0.117647   
7           Boston                Downtown             0.058824   
8           Boston             East Boston             0.083333   
9           Boston          Fenway Kenmore             0.000000   
10          Boston               Hyde Park             0.375000   
11          Boston           Jamaica Plain             0.111111   
12          Boston               North End             0.015625   
13          Boston            South Boston             0.047619   
14          Boston               South End             0.083333   
15          Boston                West End             0.187500   
16         Chicago             Albany Park             0.000000   
17         Chicago          Archer Heights             0.000000   
18         Chicago           Armour Square             0.000000   
19         Chicago                Avondale             0.000000   
20         Chicago          Belmont Cragin             0.200000   
21         Chicago                 Beverly             0.000000   
22         Chicago              Bridgeport             0.000000   
23         Chicago           Brighton Park             0.125000   
24         Chicago            Chicago Lawn             0.285714   
25         Chicago                 Douglas             0.000000   
26         Chicago               Edgewater             0.076923   
27         Chicago             Forest Glen             0.125000   
28         Chicago         Grand Boulevard             0.000000   
29         Chicago               Hegewisch             0.000000   
30         Chicago               Hyde Park             0.000000   
31         Chicago             Irving Park             0.000000   
32         Chicago          Jefferson Park             0.090909   
33         Chicago                 Kenwood             0.000000   
34         Chicago            Lincoln Park             0.028571   
35         Chicago          Lincoln Square             0.000000   
36         Chicago            Logan Square             0.000000   
37         Chicago         Lower West Side             0.000000   
38         Chicago           McKinley Park             0.000000   
39         Chicago               Montclare             0.200000   
40         Chicago         Near North Side             0.090909   
41         Chicago         Near South Side             0.058824   
42         Chicago          Near West Side             0.000000   
43         Chicago            North Center             0.052632   
44         Chicago            Portage Park             0.000000   
45         Chicago                 Pullman             0.000000   
46         Chicago               Riverdale             0.000000   
47         Chicago             Rogers Park             0.142857   
48         Chicago          South Lawndale             0.000000   
49         Chicago             South Shore             0.285714   
50         Chicago                The Loop             0.064516   
51         Chicago                  Uptown             0.062500   
52         Chicago               West Town             0.076923   
53        New York            East Village             0.020000   
54    Philadelphia             Bella Vista             0.000000   
55    Philadelphia               Bustleton             0.000000   
56    Philadelphia             Center City             0.114286   
57    Philadelphia           Chestnut Hill             0.210526   
58    Philadelphia               Fairmount             0.0666

## Look at top 10 most common venues by neighborhood

In [106]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[2:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    return row_categories_sorted.index.values[0:num_top_venues]

In [152]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['City','Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['City'] = city5_cut_grouped['City']
neighborhoods_venues_sorted['Neighborhood'] = city5_cut_grouped['Neighborhood']


for ind in np.arange(city5_cut_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 2:] = return_most_common_venues(city5_cut_grouped.iloc[ind, :], num_top_venues)
    
print (neighborhoods_venues_sorted.shape)
neighborhoods_venues_sorted.head()

(173, 12)


City Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Boston      Allston                   Bar           Pizza Place   
1  Boston     Back Bay   American Restaurant        Ice Cream Shop   
2  Boston  Bay Village                   Spa   American Restaurant   
3  Boston  Beacon Hill    Italian Restaurant   American Restaurant   
4  Boston     Brighton           Pizza Place                Bakery   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0   American Restaurant          Burger Joint           Coffee Shop   
1    Italian Restaurant                   Bar           Coffee Shop   
2    Seafood Restaurant    Italian Restaurant                  Park   
3           Pizza Place     French Restaurant             Gift Shop   
4    Chinese Restaurant           Coffee Shop             Wine Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Cocktail Bar          Gourmet Shop             Gift Shop   
1  Vietnamese Restaurant          Burger Joint    Seafood Restaurant   
2                 Bakery           Coffee Shop     French Restaurant   
3         Ice Cream Shop     Korean Restaurant    Mexican Restaurant   
4                    Bar          Dessert Shop      Greek Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0         Garden Center      French Restaurant  
1    Mexican Restaurant                 Bakery  
2    Mexican Restaurant    Arts & Crafts Store  
3          Dessert Shop                   Park  
4   American Restaurant                    Spa

## Methodology - Cluster the neighborhoods
#### Use the top ten categories by neighborhood to cluster the neighborhoods.  Setup 10 clusters and 30 iterations in k means clustering. Add cluster label to top ten table.

In [153]:
# set number of clusters
kclusters = 10

city5_cut_grouped_clustering = city5_cut_grouped.drop(['Neighborhood','City'], 1)

# run k-means clustering
kmeans = KMeans(init="k-means++", n_clusters=kclusters, n_init=30).fit(city5_cut_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]
print(len(kmeans.labels_))

173


In [154]:

# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

city5_merged = DF_NBR_LatLongs

# merge City clusters with latitude/longitude for each neighborhood
city5_merged = pd.merge(city5_merged, neighborhoods_venues_sorted, how='inner', on=['City','Neighborhood'], left_on=None, right_on=None,
         left_index=False, right_index=False, sort=True,
         suffixes=('_x', '_y'), copy=True, indicator=False,
         validate=None)




In [155]:
city5_merged # check the last columns!

City            Neighborhood   Latitude   Longitude  \
0           Boston                 Allston  42.359489  -71.142382   
1           Boston                Back Bay  42.350097  -71.086996   
2           Boston             Bay Village  42.350653  -71.069773   
3           Boston             Beacon Hill  42.358708  -71.067829   
4           Boston                Brighton  42.350097  -71.156442   
5           Boston             Charlestown  42.377875  -71.061996   
6           Boston               Chinatown  42.349814  -71.068382   
7           Boston                Downtown  42.354542  -71.057829   
8           Boston             East Boston  42.375097  -71.039217   
9           Boston          Fenway Kenmore  42.342586  -71.114255   
10          Boston               Hyde Park  42.255654  -71.124496   
11          Boston           Jamaica Plain  42.309820  -71.120330   
12          Boston               North End  42.365097  -71.054495   
13          Boston            South Boston  42.333431  -71.049495   
14          Boston               South End  42.339443  -71.084551   
15          Boston                West End  42.364746  -71.070421   
16         Chicago             Albany Park  41.968365  -87.723392   
17         Chicago          Archer Heights  41.811422  -87.726165   
18         Chicago           Armour Square  41.840033  -87.633107   
19         Chicago                Avondale  41.938921  -87.711168   
20         Chicago          Belmont Cragin  41.931698  -87.768670   
21         Chicago                 Beverly  41.718089  -87.673661   
22         Chicago              Bridgeport  41.838089  -87.651163   
23         Chicago           Brighton Park  41.818922  -87.698942   
24         Chicago            Chicago Lawn  41.775033  -87.696441   
25         Chicago                 Douglas  41.834756  -87.618106   
26         Chicago               Edgewater  41.983365  -87.663945   
27         Chicago             Forest Glen  41.991701  -87.793395   
28         Chicago         Grand Boulevard  41.813923  -87.617272   
29         Chicago               Hegewisch  41.653646  -87.546988   
30         Chicago               Hyde Park  41.794201  -87.593938   
31         Chicago             Irving Park  41.953365  -87.736447   
32         Chicago          Jefferson Park  41.970587  -87.763393   
33         Chicago                 Kenwood  41.809201  -87.597549   
34         Chicago            Lincoln Park  41.921699  -87.647832   
35         Chicago          Lincoln Square  41.975865  -87.689224   
36         Chicago            Logan Square  41.923365  -87.699223   
37         Chicago         Lower West Side  41.854200  -87.665609   
38         Chicago           McKinley Park  41.831700  -87.673664   
39         Chicago               Montclare  41.927878  -87.815590   
40         Chicago         Near North Side  41.900033  -87.634497   
41         Chicago         Near South Side  41.856700  -87.624774   
42         Chicago          Near West Side  41.880033  -87.666720   
43         Chicago            North Center  41.953921  -87.678945   
44         Chicago            Portage Park  41.957809  -87.765059   
45         Chicago                 Pullman  41.957809  -87.765059   
46         Chicago               Riverdale  41.957809  -87.765059   
47         Chicago             Rogers Park  42.008643  -87.666724   
48         Chicago          South Lawndale  41.843644  -87.712554   
49         Chicago             South Shore  41.761979  -87.577825   
50         Chicago                The Loop  41.878971  -87.637882   
51         Chicago                  Uptown  41.981699  -87.659778   
52         Chicago               West Town  41.901421  -87.686166   
53        New York            East Village  40.727847  -73.982226   
54    Philadelphia             Bella Vista  39.935391  -75.157122   
55    Philadelphia               Bustleton  40.082611  -75.031560   
56    Philadelphia             Center City  39.952449  -75.166441   
57    Philad

#### East Village is in cluster 3.

In [156]:
city5_merged[city5_merged['Neighborhood'] == 'East Village']

City  Neighborhood   Latitude  Longitude  Cluster Labels  \
53  New York  East Village  40.727847 -73.982226               3   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
53                   Bar              Wine Bar        Ice Cream Shop   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
53    Mexican Restaurant    Chinese Restaurant           Pizza Place   

   7th Most Common Venue          8th Most Common Venue 9th Most Common Venue  \
53          Cocktail Bar  Vegetarian / Vegan Restaurant           Coffee Shop   

   10th Most Common Venue  
53    Japanese Restaurant

#### Quick glance at each cluster.

In [157]:
city5_merged[city5_merged['Cluster Labels'] == 0]

City            Neighborhood   Latitude   Longitude  \
10          Boston               Hyde Park  42.255654  -71.124496   
24         Chicago            Chicago Lawn  41.775033  -87.696441   
39         Chicago               Montclare  41.927878  -87.815590   
47         Chicago             Rogers Park  42.008643  -87.666724   
49         Chicago             South Shore  41.761979  -87.577825   
57    Philadelphia           Chestnut Hill  40.077055  -75.207400   
65    Philadelphia  Northeast Philadelphia  40.050674  -75.066800   
69    Philadelphia                Powelton  39.958446  -75.191012   
159  San Francisco        Presidio Heights  37.788693 -122.457541   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
10                0   American Restaurant           Pizza Place   
24                0           Pizza Place   American Restaurant   
39                0   American Restaurant                Bakery   
47                0   American Restaurant                   Bar   
49                0   American Restaurant           Pizza Place   
57                0   American Restaurant           Coffee Shop   
65                0   American Restaurant           Pizza Place   
69                0           Pizza Place   American Restaurant   
159               0   American Restaurant    Italian Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
10         Ice Cream Shop    Italian Restaurant                   Bar   
24     Mexican Restaurant             Gift Shop         Garden Center   
39                    Bar                  Park           Coffee Shop   
47            Pizza Place           Coffee Shop                  Park   
49     Seafood Restaurant           Record Shop                  Park   
57      French Restaurant           Pizza Place                Bakery   
65         Farmers Market    Chinese Restaurant           Art Gallery   
69            Coffee Shop                   Bar          Burger Joint   
159                  Park           Coffee Shop          Cocktail Bar   

         6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
10            Arepa Restaurant           Coffee Shop             Gift Shop   
24           French Restaurant           Flower Shop   Filipino Restaurant   
39                 Pizza Place          Cocktail Bar             Gift Shop   
47                   Gift Shop    Italian Restaurant        Farmers Market   
49            Arepa Restaurant    Chinese Restaurant         Garden Center   
57                         Bar                   Spa        Ice Cream Shop   
65                 Coffee Shop          Gourmet Shop             Gift Shop   
69   Middle Eastern Restaurant          Dessert Shop                  Park   
159                  Gift Shop         Garden Center     French Restaurant   

    9th Most Common Venue 10th Most Common Venue  
10          Garden Center      French Restaurant  
24         Farmers Market                Dog Run  
39          Garden Center      French Restaurant  
47     Mexican Restaurant       Greek Restaurant  
49      French Restaurant            Flower Shop  
57     Italian Restaurant            Record Shop  
65          Garden Center      French Restaurant  
69       Arepa Restaurant              Gift Shop  
159           Flower Shop    Filipino Restaurant

In [158]:
city5_merged[city5_merged['Cluster Labels'] == 1]

City     Neighborhood   Latitude   Longitude  Cluster Labels  \
3           Boston      Beacon Hill  42.358708  -71.067829               1   
12          Boston        North End  42.365097  -71.054495               1   
15          Boston         West End  42.364746  -71.070421               1   
21         Chicago          Beverly  41.718089  -87.673661               1   
27         Chicago      Forest Glen  41.991701  -87.793395               1   
44         Chicago     Portage Park  41.957809  -87.765059               1   
45         Chicago          Pullman  41.957809  -87.765059               1   
46         Chicago        Riverdale  41.957809  -87.765059               1   
72    Philadelphia         Somerton  40.123443  -75.014892               1   
150  San Francisco  Mission Terrace  37.724358 -122.446749               1   
158  San Francisco       Polk Gulch  37.792353 -122.429786               1   
167  San Francisco   Telegraph Hill  37.801667 -122.410576               1   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
3      Italian Restaurant   American Restaurant           Pizza Place   
12     Italian Restaurant           Pizza Place                Bakery   
15    American Restaurant    Italian Restaurant     French Restaurant   
21     Italian Restaurant             Juice Bar                Bakery   
27    American Restaurant                   Bar    Italian Restaurant   
44     Italian Restaurant               Dog Run           Pizza Place   
45     Italian Restaurant               Dog Run           Pizza Place   
46     Italian Restaurant               Dog Run           Pizza Place   
72     Italian Restaurant     French Restaurant            Bagel Shop   
150   American Restaurant           Flower Shop          Dessert Shop   
158             Wine Shop            Beer Store        Ice Cream Shop   
167    Italian Restaurant           Pizza Place           Coffee Shop   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
3       French Restaurant             Gift Shop        Ice Cream Shop   
12     Seafood Restaurant           Coffee Shop                  Park   
15                   Park          Gourmet Shop    Mexican Restaurant   
21           Burger Joint                  Park             Wine Shop   
27                Dog Run                  Park            Beer Store   
44         Ice Cream Shop        Farmers Market    Mexican Restaurant   
45         Ice Cream Shop        Farmers Market    Mexican Restaurant   
46         Ice Cream Shop        Farmers Market    Mexican Restaurant   
72                    Spa    Chinese Restaurant             Wine Shop   
150          Burger Joint                  Park          Cocktail Bar   
158    Italian Restaurant             Juice Bar               Dog Run   
167                  Park    Chinese Restaurant                Bakery   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
3       Korean Restaurant    Mexican Restaurant          Dessert Shop   
12    American Restaurant                   Spa           Record Shop   
15            Coffee Shop           Pizza Place             Gift Shop   
21            Coffee Shop             Gift Shop         Garden Center   
27                    Spa            Hobby Shop                Bakery   
44                   Park          Cocktail Bar         Garden Center   
45                   Park          Cocktail Bar         Garden Center   
46                   Park          Cocktail Bar         Garden Center   
72           Cocktail Bar             Gift Shop         Garden Center   
150          Gourmet Shop             Gift Shop         Garden Center   
158                  Park           Coffee Shop             Gift Shop   
167    Mexican Restaurant          Cocktail Bar        Ice Cream Shop   

    10th Most Common Venue  
3                     Park  
12          Ice Cream Shop  
15              Bagel Shop  
21       French Restaurant  
27  

In [159]:
city5_merged[city5_merged['Cluster Labels'] == 2]

City        Neighborhood   Latitude   Longitude  Cluster Labels  \
11          Boston       Jamaica Plain  42.309820  -71.120330               2   
28         Chicago     Grand Boulevard  41.813923  -87.617272               2   
30         Chicago           Hyde Park  41.794201  -87.593938               2   
50         Chicago            The Loop  41.878971  -87.637882               2   
76    Philadelphia     University City  39.949279  -75.189624               2   
78     Portland OR            Brooklyn  45.490397 -122.637317               2   
81     Portland OR  Creston Kenilworth  45.494136 -122.637626               2   
85     Portland OR   Hosford Abernethy  45.505286 -122.670658               2   
87     Portland OR              Kenton  45.581784 -122.681486               2   
93     Portland OR           Multnomah  45.469563 -122.707318               2   
120  San Francisco         Cole Valley  37.764859 -122.458546               2   
139  San Francisco    Little Hollywood  37.711963 -122.402699               2   
155  San Francisco  North of Panhandle  37.776317 -122.446729               2   
161  San Francisco         Rincon Hill  37.786871 -122.396164               2   

    1st Most Common Venue 2nd Most Common Venue  3rd Most Common Venue  \
11            Art Gallery                Bakery            Coffee Shop   
28            Coffee Shop           Art Gallery                   Park   
30            Coffee Shop             Wine Shop                 Bakery   
50            Coffee Shop    Italian Restaurant     Mexican Restaurant   
76            Coffee Shop   American Restaurant                 Bakery   
78            Coffee Shop          Cocktail Bar    Japanese Restaurant   
81            Coffee Shop          Cocktail Bar               Wine Bar   
85            Coffee Shop   American Restaurant                    Bar   
87            Coffee Shop           Pizza Place            Art Gallery   
93            Coffee Shop   American Restaurant                 Bakery   
120               Dog Run           Coffee Shop            Pizza Place   
139           Coffee Shop                  Park  Vietnamese Restaurant   
155           Coffee Shop    Mexican Restaurant    Arts & Crafts Store   
161           Coffee Shop   American Restaurant           Cocktail Bar   

         4th Most Common Venue      5th Most Common Venue  \
11         American Restaurant         Seafood Restaurant   
28                   Wine Shop               Cocktail Bar   
30           French Restaurant  Middle Eastern Restaurant   
50         American Restaurant               Burger Joint   
76                  Beer Store                       Park   
78          Mexican Restaurant                       Park   
81         Japanese Restaurant         Mexican Restaurant   
85                        Park               Cocktail Bar   
87                   Wine Shop               Gourmet Shop   
93                         Bar                Pizza Place   
120                Art Gallery  Middle Eastern Restaurant   
139                Art Gallery                  Wine Shop   
155  Middle Eastern Restaurant                    Dog Run   
161         Seafood Restaurant                  Juice Bar   

    6th Most Common Venue 7th Most Common Venue  \
11            Pizza Place          Cocktail Bar   
28           Gourmet Shop             Gift Shop   
30                   Park           Pizza Place   
50            Pizza Place             Juice Bar   
76           Gourmet Shop             Gift Shop   
78       Greek Restaurant             Gift Shop   
81           Burger Joint                  Park   
85           Gourmet Shop             Gift Shop   
87              Gift Shop         Garden Center   
93           Cocktail Bar          Gourmet Shop   
120                  Park          Cocktail Bar   
139          Cocktail Bar             Gift Shop   
155                  Park             Wine Shop   
161                   Bar           Art Gallery   

     

In [160]:
city5_merged[city5_merged['Cluster Labels'] == 3]

City           Neighborhood   Latitude   Longitude  \
1           Boston               Back Bay  42.350097  -71.086996   
2           Boston            Bay Village  42.350653  -71.069773   
6           Boston              Chinatown  42.349814  -71.068382   
7           Boston               Downtown  42.354542  -71.057829   
14          Boston              South End  42.339443  -71.084551   
26         Chicago              Edgewater  41.983365  -87.663945   
32         Chicago         Jefferson Park  41.970587  -87.763393   
34         Chicago           Lincoln Park  41.921699  -87.647832   
36         Chicago           Logan Square  41.923365  -87.699223   
40         Chicago        Near North Side  41.900033  -87.634497   
41         Chicago        Near South Side  41.856700  -87.624774   
51         Chicago                 Uptown  41.981699  -87.659778   
52         Chicago              West Town  41.901421  -87.686166   
53        New York           East Village  40.727847  -73.982226   
54    Philadelphia            Bella Vista  39.935391  -75.157122   
56    Philadelphia            Center City  39.952449  -75.166441   
62    Philadelphia                  Logan  40.028445  -75.151565   
66    Philadelphia     Northern Liberties  39.965946  -75.146288   
70    Philadelphia          Queen Village  39.934280  -75.148510   
74    Philadelphia                 Tacony  40.031223  -75.044339   
75    Philadelphia                  Tioga  40.009001  -75.167956   
77     Portland OR                  Boise  45.549109 -122.678953   
83     Portland OR              Hillsdale  45.481507 -122.694818   
91     Portland OR             Montavilla  45.519008 -122.578982   
92     Portland OR              Mt. Tabor  45.514292 -122.616607   
94     Portland OR     Old Town Chinatown  45.525317 -122.681385   
95     Portland OR         Pearl District  45.530447 -122.689350   
96     Portland OR      Portland Downtown  45.523452 -122.676207   
99     Portland OR               Richmond  45.504440 -122.631318   
100    Portland OR         Rose City Park  45.537814 -122.623149   
102    Portland OR                  Sabin  45.552989 -122.657579   
103    Portland OR      Sellwood Moreland  45.464564 -122.652595   
104    Portland OR        Sullivans Gulch  45.531934 -122.651367   
109    Portland OR              Woodstock  45.479008 -122.608427   
111  San Francisco             Anza Vista  37.781004 -122.444436   
114  San Francisco         Bernal Heights  37.739540 -122.418049   
116  San Francisco         Cathedral Hill  37.784344 -122.426738   
117  San Francisco            China Basin  37.779502 -122.394993   
118  San Francisco              Chinatown  37.796596 -122.408582   
119  San Francisco           Civic Center  37.778972 -122.420653   
122  San Francisco        Design District  37.768924 -122.403910   
123  San Francisco        Dolores Heights  37.756947 -122.437816   
124  San Francisco        Duboce Triangle  37.766159 -122.435493   
126  San Francisco              Excelsior  37.724133 -122.438455   
128  San Francisco     Financial District  37.792773 -122.409847   
131  San Francisco         Haight Ashbury  37.769930 -122.446916   
132  San Francisco           Hayes Valley  37.774713 -122.429710   
133  San Francisco              Ingleside  37.722987 -122.453027   
136  San Francisco            Jordan Park  37.783794 -122.460746   
137  San Francisco               Lakeside  37.725884 -122.482213   
138  San Francisco         Laurel Heights  37.784418 -122.454827   
140  San Francisco          Little Russia  37.780238 -122.485924   
141  San Francisco          Lone Mountain  37.778345 -122.457045   
142  San Francisco           Lower Haight  37.771721 -122.438088   
143  San Francisco         Lower Nob Hill  37.789084 -122.418035   
144  San Francisco  Lower Pacific Heights  37.786292 -122.444531   
147  San Francisco             Mid Market  37.780153 -122.415837   
148  San Francisco            Mission Bay  37.771456 -122.399293   
14

In [161]:
city5_merged[city5_merged['Cluster Labels'] == 4]

City      Neighborhood   Latitude   Longitude  Cluster Labels  \
25         Chicago           Douglas  41.834756  -87.618106               4   
58    Philadelphia         Fairmount  39.972335  -75.181012               4   
80     Portland OR         Concordia  45.566009 -122.649712               4   
112  San Francisco   Ashbury Heights  37.762847 -122.451533               4   
115  San Francisco            Castro  37.762771 -122.439926               4   
125  San Francisco     Eureka Valley  37.760931 -122.448007               4   
129  San Francisco  Fishermans Wharf  37.808110 -122.425386               4   
130  San Francisco         Glen Park  37.737910 -122.436481               4   
135  San Francisco      Inner Sunset  37.757526 -122.473058               4   
146  San Francisco      Merced Manor  37.733333 -122.477222               4   
153  San Francisco        Noe Valley  37.749055 -122.443232               4   
157  San Francisco        Parkmerced  37.718333 -122.480556               4   
170  San Francisco     Vista del Mar  37.742986 -122.436638               4   

    1st Most Common Venue          2nd Most Common Venue  \
25                   Park                 Ice Cream Shop   
58                   Park                    Pizza Place   
80                   Park                    Pizza Place   
112                  Park                       Wine Bar   
115                  Park                        Dog Run   
125                  Park                       Wine Bar   
129                  Park                      Gift Shop   
130                  Park                    Coffee Shop   
135                  Park  Vegetarian / Vegan Restaurant   
146                  Park          Vietnamese Restaurant   
153                  Park            American Restaurant   
157                  Park                   Cocktail Bar   
170               Dog Run                           Park   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
25     Seafood Restaurant                   Spa           Pizza Place   
58            Coffee Shop          Burger Joint    Italian Restaurant   
80               Wine Bar                Bakery               Dog Run   
112           Coffee Shop        Ice Cream Shop    Mexican Restaurant   
115         Hot Dog Joint           Pizza Place   Arts & Crafts Store   
125           Art Gallery                Bakery       Organic Grocery   
129        Ice Cream Shop           Art Gallery    Seafood Restaurant   
130           Pizza Place           Cheese Shop     French Restaurant   
135                   Bar           Coffee Shop             Wine Shop   
146           Art Gallery   Japanese Restaurant        Farmers Market   
153               Dog Run           Coffee Shop          Cocktail Bar   
157             Juice Bar    Mexican Restaurant               Dog Run   
170           Coffee Shop             Wine Shop          Cocktail Bar   

         6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
25                 Art Gallery           Flower Shop   Filipino Restaurant   
58                     Dog Run    Chinese Restaurant           Record Shop   
80                Cocktail Bar             Gift Shop         Garden Center   
112  Middle Eastern Restaurant       Organic Grocery           Cheese Shop   
115                     Bakery          Dessert Shop              Wine Bar   
125                  Wine Shop           Coffee Shop             Gift Shop   
129               Gourmet Shop   Arts & Crafts Store                   Bar   
130         Italian Restaurant    Mexican Restaurant               Dog Run   
135               Cocktail Bar             Gift Shop         Garden Center   
146                  Wine Shop          Cocktail Bar             Gift Shop   
153               Gourmet Shop             Gift Shop         Garden Center   
157                Coffee Shop      Greek Restaurant             Gift Shop   
170               Gourmet Sho

In [162]:
city5_merged[city5_merged['Cluster Labels'] == 5]

City         Neighborhood   Latitude   Longitude  \
4           Boston             Brighton  42.350097  -71.156442   
5           Boston          Charlestown  42.377875  -71.061996   
13          Boston         South Boston  42.333431  -71.049495   
59    Philadelphia            Frankford  40.028167  -75.084896   
60    Philadelphia           Holmesburg  40.041500  -75.027949   
61    Philadelphia         Hunting Park  40.016501  -75.143788   
64    Philadelphia               Mantua  39.962613  -75.191290   
71    Philadelphia           Roxborough  40.038167  -75.222402   
84     Portland OR            Hollywood  45.534669 -122.628916   
98     Portland OR  Powellhurst Gilbert  45.504009 -122.537592   
108    Portland OR             Woodlawn  45.573733 -122.661193   
113  San Francisco              Bayview  37.734097 -122.391360   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
4                 5           Pizza Place                Bakery   
5                 5           Pizza Place           Coffee Shop   
13                5           Pizza Place    Chinese Restaurant   
59                5           Pizza Place    Chinese Restaurant   
60                5           Pizza Place    Italian Restaurant   
61                5           Pizza Place                  Park   
64                5           Pizza Place                Bakery   
71                5           Pizza Place    Chinese Restaurant   
84                5           Pizza Place           Coffee Shop   
98                5           Pizza Place    Chinese Restaurant   
108               5           Coffee Shop           Pizza Place   
113               5                Bakery           Pizza Place   

         3rd Most Common Venue 4th Most Common Venue  \
4           Chinese Restaurant           Coffee Shop   
5           Italian Restaurant   Moroccan Restaurant   
13                         Bar    Italian Restaurant   
59                   Gift Shop                   Bar   
60                      Bakery                   Bar   
61                   Wine Shop             Gift Shop   
64   Middle Eastern Restaurant                  Park   
71          Mexican Restaurant                   Bar   
84              Ice Cream Shop                Bakery   
98          Mexican Restaurant           Coffee Shop   
108         Italian Restaurant   Arts & Crafts Store   
113         Mexican Restaurant                  Park   

         5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
4                    Wine Shop                   Bar          Dessert Shop   
5                         Park          Gourmet Shop         Garden Center   
13                 Coffee Shop        Ice Cream Shop    Mexican Restaurant   
59                 Coffee Shop          Gourmet Shop         Garden Center   
60          Seafood Restaurant           Coffee Shop          Cocktail Bar   
61               Garden Center     French Restaurant           Flower Shop   
64          Chinese Restaurant           Coffee Shop          Cocktail Bar   
71                 Coffee Shop             Gift Shop         Garden Center   
84   Middle Eastern Restaurant    Chinese Restaurant          Cocktail Bar   
98                   Gift Shop         Garden Center     French Restaurant   
108                     Bakery                   Bar             Wine Shop   
113         Chinese Restaurant          Cocktail Bar             Gift Shop   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
4        Greek Restaurant   American Restaurant                    Spa  
5       French Restaurant           Flower Shop    Filipino Restaurant  
13                Dog Run          Dessert Shop                   Park  
59      French Restaurant           Flower Shop    Filipino Restaurant  
60              Gift Shop         Garden Center      French Restaurant  
61    Filipino Restaurant        Farmers Market                Dog Run  
64              Gift Shop   

In [163]:
city5_merged[city5_merged['Cluster Labels'] == 6]

City          Neighborhood   Latitude   Longitude  \
8           Boston           East Boston  42.375097  -71.039217   
18         Chicago         Armour Square  41.840033  -87.633107   
19         Chicago              Avondale  41.938921  -87.711168   
22         Chicago            Bridgeport  41.838089  -87.651163   
29         Chicago             Hegewisch  41.653646  -87.546988   
33         Chicago               Kenwood  41.809201  -87.597549   
55    Philadelphia             Bustleton  40.082611  -75.031560   
68    Philadelphia          Point Breeze  39.933446  -75.177956   
107    Portland OR  West Portland ParkÂ   45.446785 -122.725652   
134  San Francisco    Ingleside Terraces  37.724167 -122.466389   
163  San Francisco    Saint Francis Wood  37.734653 -122.468027   
166  San Francisco       Sunset District  37.753542 -122.495250   
171  San Francisco           West Portal  37.737500 -122.472778   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
8                 6           Pizza Place    Mexican Restaurant   
18                6    Chinese Restaurant                Bakery   
19                6    Chinese Restaurant                  Park   
22                6    Chinese Restaurant                  Park   
29                6           Pizza Place                   Bar   
33                6           Pizza Place    Chinese Restaurant   
55                6           Pizza Place    Seafood Restaurant   
68                6    Chinese Restaurant                   Bar   
107               6    Chinese Restaurant                   Bar   
134               6    Chinese Restaurant   Japanese Restaurant   
163               6    Chinese Restaurant           Pizza Place   
166               6    Chinese Restaurant   Japanese Restaurant   
171               6           Pizza Place    Chinese Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
8      Chinese Restaurant           Art Gallery    Seafood Restaurant   
18     Italian Restaurant         Hot Dog Joint           Art Gallery   
19                    Bar     Korean Restaurant         Hot Dog Joint   
22            Coffee Shop     Korean Restaurant           Pizza Place   
29     Mexican Restaurant                  Park    Chinese Restaurant   
33            Art Gallery    Seafood Restaurant                  Park   
55     Italian Restaurant    Chinese Restaurant            Hobby Shop   
68            Coffee Shop           Pizza Place   American Restaurant   
107                  Park           Coffee Shop          Cocktail Bar   
134           Coffee Shop          Cocktail Bar          Gourmet Shop   
163              Wine Bar           Flower Shop                  Park   
166          Dessert Shop     Korean Restaurant                   Bar   
171                  Park         Garden Center              Wine Bar   

    6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
8                    Park   American Restaurant  Vietnamese Restaurant   
18           Cupcake Shop          Gourmet Shop       Arepa Restaurant   
19    Arts & Crafts Store            Bagel Shop              Gift Shop   
22     Italian Restaurant           Art Gallery     Mexican Restaurant   
29           Cocktail Bar             Gift Shop          Garden Center   
33              Gift Shop         Garden Center      French Restaurant   
55    Arts & Crafts Store           Coffee Shop              Gift Shop   
68    Arts & Crafts Store            Bagel Shop           Gourmet Shop   
107          Gourmet Shop             Gift Shop          Garden Center   
134             Gift Shop         Garden Center      French Restaurant   
163           Coffee Shop      Greek Restaurant           Cocktail Bar   
166           Pizza Place        Ice Cream Shop  Vietnamese Restaurant   
171    Italian Restaurant           Coffee Shop       Greek Restaurant   

    9th Most Common Venue 10th Most Common Venue  
8              Bagel Shop

In [164]:
city5_merged[city5_merged['Cluster Labels'] == 7]

City        Neighborhood   Latitude   Longitude  Cluster Labels  \
0           Boston             Allston  42.359489  -71.142382               7   
31         Chicago         Irving Park  41.953365  -87.736447               7   
35         Chicago      Lincoln Square  41.975865  -87.689224               7   
42         Chicago      Near West Side  41.880033  -87.666720               7   
43         Chicago        North Center  41.953921  -87.678945               7   
63    Philadelphia            Manayunk  40.024557  -75.214068               7   
73    Philadelphia  South Philadelphia  39.921566  -75.175834               7   
79     Portland OR             Buckman  45.517564 -122.661919               7   
86     Portland OR            Humboldt  45.560528 -122.680381               7   
88     Portland OR                King  45.557369 -122.675249               7   
89     Portland OR         Laurelhurst  45.526986 -122.633448               7   
90     Portland OR       Madison South  45.542603 -122.594795               7   
97     Portland OR          Portsmouth  45.586668 -122.738096               7   
101    Portland OR             Roseway  45.548290 -122.597749               7   
105    Portland OR           Sunnyside  45.515682 -122.633499               7   
106    Portland OR              Vernon  45.562037 -122.657742               7   
110  San Francisco        Alamo Square  37.777745 -122.437731               7   
127  San Francisco            Fillmore  37.780811 -122.438462               7   

     1st Most Common Venue 2nd Most Common Venue  \
0                      Bar           Pizza Place   
31             Coffee Shop                   Bar   
35                     Bar           Pizza Place   
42             Pizza Place                   Bar   
43                     Bar           Coffee Shop   
63                     Bar           Pizza Place   
73             Pizza Place                   Bar   
79                     Bar           Coffee Shop   
86                     Bar           Coffee Shop   
88                     Bar           Pizza Place   
89                     Bar    Mexican Restaurant   
90   Vietnamese Restaurant           Pizza Place   
97                     Bar        Ice Cream Shop   
101  Vietnamese Restaurant                   Bar   
105            Coffee Shop                   Bar   
106                    Bar           Coffee Shop   
110                    Bar    Mexican Restaurant   
127                    Bar                Bakery   

             3rd Most Common Venue 4th Most Common Venue  \
0              American Restaurant          Burger Joint   
31                     Pizza Place    Chinese Restaurant   
35               Korean Restaurant        Ice Cream Shop   
42              Mexican Restaurant               Dog Run   
43             American Restaurant    Seafood Restaurant   
63                       Speakeasy          Dessert Shop   
73              Italian Restaurant    Chinese Restaurant   
79              Mexican Restaurant             Juice Bar   
86                     Flower Shop             Speakeasy   
88                       Gift Shop    Seafood Restaurant   
89                     Pizza Place                   Spa   
90                             Bar    Mexican Restaurant   
97                        Beer Bar           Coffee Shop   
101                    Coffee Shop           Pizza Place   
105  Vegetarian / Vegan Restaurant          Cocktail Bar   
106                   Cocktail Bar             Juice Bar   
110                      Gift Shop    Seafood Restaurant   
127            Arts & Crafts Store    Mexican Restaurant   

    5th Most Common Venue      6th Most Common Venue  7th Most Common Venue  \
0             Coffee Shop               Cocktail Bar           Gourmet Shop   
31       Tapas Restaurant                  Wine Shop              Gift Shop   
35     Italian Restaurant         Mexican Restaurant                   Park   
42                   Park   

In [165]:
city5_merged[city5_merged['Cluster Labels'] == 8]

City     Neighborhood   Latitude   Longitude  Cluster Labels  \
16         Chicago      Albany Park  41.968365  -87.723392               8   
17         Chicago   Archer Heights  41.811422  -87.726165               8   
20         Chicago   Belmont Cragin  41.931698  -87.768670               8   
23         Chicago    Brighton Park  41.818922  -87.698942               8   
37         Chicago  Lower West Side  41.854200  -87.665609               8   
38         Chicago    McKinley Park  41.831700  -87.673664               8   
48         Chicago   South Lawndale  41.843644  -87.712554               8   
121  San Francisco   Crocker Amazon  37.712232 -122.447553               8   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
16     Mexican Restaurant           Pizza Place     Korean Restaurant   
17     Mexican Restaurant         Hot Dog Joint           Coffee Shop   
20     Mexican Restaurant   American Restaurant    Chinese Restaurant   
23     Mexican Restaurant           Pizza Place          Burger Joint   
37     Mexican Restaurant                Bakery           Pizza Place   
38     Mexican Restaurant    Seafood Restaurant          Burger Joint   
48     Mexican Restaurant           Pizza Place          Dessert Shop   
121    Mexican Restaurant    Chinese Restaurant                Bakery   

      4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
16       Seafood Restaurant           Coffee Shop                  Park   
17                   Bakery                   Bar          Gourmet Shop   
20   Argentinian Restaurant           Art Gallery          Gourmet Shop   
23                     Park   American Restaurant   Arts & Crafts Store   
37              Coffee Shop        Ice Cream Shop           Flower Shop   
38              Coffee Shop    Chinese Restaurant             Wine Shop   
48                Wine Shop             Gift Shop         Garden Center   
121                    Park          Cocktail Bar             Gift Shop   

      7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
16       Chinese Restaurant         Garden Center     French Restaurant   
17                Gift Shop         Garden Center     French Restaurant   
20                Gift Shop         Garden Center     French Restaurant   
23   Argentinian Restaurant             Gift Shop         Garden Center   
37                      Bar            Beer Store          Dessert Shop   
38             Cocktail Bar             Gift Shop         Garden Center   
48        French Restaurant           Flower Shop   Filipino Restaurant   
121           Garden Center     French Restaurant           Flower Shop   

    10th Most Common Venue  
16             Flower Shop  
17             Flower Shop  
20             Flower Shop  
23       French Restaurant  
37               Gift Shop  
38       French Restaurant  
48          Farmers Market  
121    Filipino Restaurant

In [166]:
city5_merged[city5_merged['Cluster Labels'] == 9]

City     Neighborhood   Latitude   Longitude  Cluster Labels  \
9           Boston   Fenway Kenmore  42.342586  -71.114255               9   
67    Philadelphia            Olney  40.041223  -75.123786               9   
82     Portland OR       Grant Park  45.539413 -122.635797               9   
145  San Francisco  Marina District  37.803835 -122.446229               9   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
9                    Park             Wine Shop          Cocktail Bar   
67      Korean Restaurant                  Park           Pizza Place   
82                   Park           Pizza Place    Mexican Restaurant   
145                  Park          Gourmet Shop                   Spa   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
9            Gourmet Shop             Gift Shop         Garden Center   
67       Greek Restaurant             Gift Shop         Garden Center   
82                    Spa    Chinese Restaurant         Garden Center   
145           Coffee Shop    Chinese Restaurant             Gift Shop   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
9       French Restaurant           Flower Shop   Filipino Restaurant   
67      French Restaurant           Flower Shop   Filipino Restaurant   
82      French Restaurant           Flower Shop   Filipino Restaurant   
145         Garden Center     French Restaurant           Flower Shop   

    10th Most Common Venue  
9           Farmers Market  
67          Farmers Market  
82          Farmers Market  
145    Filipino Restaurant

## Look at  each city map with clusters.  Review list of neighborhoods in each city in cluster 3.

In [177]:
city5_merged[(city5_merged['Cluster Labels'] == 3) & (city5_merged['City'] == 'Philadelphia')]

City        Neighborhood   Latitude  Longitude  Cluster Labels  \
54  Philadelphia         Bella Vista  39.935391 -75.157122               3   
56  Philadelphia         Center City  39.952449 -75.166441               3   
62  Philadelphia               Logan  40.028445 -75.151565               3   
66  Philadelphia  Northern Liberties  39.965946 -75.146288               3   
70  Philadelphia       Queen Village  39.934280 -75.148510               3   
74  Philadelphia              Tacony  40.031223 -75.044339               3   
75  Philadelphia               Tioga  40.009001 -75.167956               3   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
54  Vietnamese Restaurant    Mexican Restaurant    Italian Restaurant   
56    American Restaurant                Bakery                   Spa   
62     Seafood Restaurant           Pizza Place        Ice Cream Shop   
66            Coffee Shop   Arts & Crafts Store   American Restaurant   
70  Vietnamese Restaurant           Coffee Shop         Hot Dog Joint   
74            Flower Shop           Pizza Place        Ice Cream Shop   
75           Dessert Shop           Pizza Place    Chinese Restaurant   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
54           Coffee Shop           Pizza Place                   Bar   
56    Italian Restaurant           Coffee Shop    Seafood Restaurant   
62                Bakery                   Bar           Coffee Shop   
66    Chinese Restaurant           Flower Shop   Japanese Restaurant   
70                  Park           Art Gallery                   Bar   
74                Bakery        Farmers Market             Wine Shop   
75             Gift Shop        Ice Cream Shop    Seafood Restaurant   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
54                Bakery          Gourmet Shop           Art Gallery   
56          Dessert Shop    Chinese Restaurant           Pizza Place   
62          Cocktail Bar             Gift Shop         Garden Center   
66    Mexican Restaurant               Dog Run                  Park   
70            Beer Store    Chinese Restaurant               Dog Run   
74             Gift Shop         Garden Center     French Restaurant   
75         Garden Center     French Restaurant           Flower Shop   

   10th Most Common Venue  
54      French Restaurant  
56           Gourmet Shop  
62      French Restaurant  
66            Pizza Place  
70             Hobby Shop  
74    Filipino Restaurant  
75    Filipino Restaurant

In [169]:
address = 'Philadelphia, PA'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)


rainbow = ['#8000ff', '#000080', '#10a2f0', '#2adddd', '#00ff00', '#fb8662', '#0b6623', '#ffa256', '#ff72be', '#ff0000']

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(city5_merged['Latitude'], city5_merged['Longitude'], city5_merged['Neighborhood'], city5_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [176]:
city5_merged[(city5_merged['Cluster Labels'] == 3) & (city5_merged['City'] == 'Boston')]

City Neighborhood   Latitude  Longitude  Cluster Labels  \
1   Boston     Back Bay  42.350097 -71.086996               3   
2   Boston  Bay Village  42.350653 -71.069773               3   
6   Boston    Chinatown  42.349814 -71.068382               3   
7   Boston     Downtown  42.354542 -71.057829               3   
14  Boston    South End  42.339443 -71.084551               3   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
1    American Restaurant        Ice Cream Shop    Italian Restaurant   
2                    Spa   American Restaurant    Seafood Restaurant   
6    American Restaurant                   Spa    Italian Restaurant   
7            Coffee Shop                  Park                Bakery   
14                Bakery           Coffee Shop   American Restaurant   

   4th Most Common Venue      5th Most Common Venue  6th Most Common Venue  \
1                    Bar                Coffee Shop  Vietnamese Restaurant   
2     Italian Restaurant                       Park                 Bakery   
6     Seafood Restaurant                Pizza Place                 Bakery   
7     Italian Restaurant        American Restaurant           Burger Joint   
14    Italian Restaurant  Middle Eastern Restaurant            Pizza Place   

   7th Most Common Venue 8th Most Common Venue  9th Most Common Venue  \
1           Burger Joint    Seafood Restaurant     Mexican Restaurant   
2            Coffee Shop     French Restaurant     Mexican Restaurant   
6      French Restaurant    Mexican Restaurant                   Park   
7     Chinese Restaurant              Wine Bar           Cocktail Bar   
14   Arts & Crafts Store          Burger Joint  Vietnamese Restaurant   

   10th Most Common Venue  
1                  Bakery  
2     Arts & Crafts Store  
6     Arts & Crafts Store  
7          Farmers Market  
14     Chinese Restaurant

In [170]:
address = 'Boston, MA'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=13)

rainbow =  ['#8000ff', '#000080', '#10a2f0', '#2adddd', '#00ff00', '#fb8662', '#0b6623', '#ffa256', '#ff72be', '#ff0000']

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(city5_merged['Latitude'], city5_merged['Longitude'], city5_merged['Neighborhood'], city5_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [178]:
city5_merged[(city5_merged['Cluster Labels'] == 3) & (city5_merged['City'] == 'Chicago')]

City     Neighborhood   Latitude  Longitude  Cluster Labels  \
26  Chicago        Edgewater  41.983365 -87.663945               3   
32  Chicago   Jefferson Park  41.970587 -87.763393               3   
34  Chicago     Lincoln Park  41.921699 -87.647832               3   
36  Chicago     Logan Square  41.923365 -87.699223               3   
40  Chicago  Near North Side  41.900033 -87.634497               3   
41  Chicago  Near South Side  41.856700 -87.624774               3   
51  Chicago           Uptown  41.981699 -87.659778               3   
52  Chicago        West Town  41.901421 -87.686166               3   

   1st Most Common Venue  2nd Most Common Venue 3rd Most Common Venue  \
26    Mexican Restaurant            Coffee Shop   American Restaurant   
32        Ice Cream Shop            Coffee Shop                   Bar   
34           Pizza Place                    Bar           Coffee Shop   
36          Cocktail Bar     Mexican Restaurant                   Bar   
40             Wine Shop            Pizza Place           Art Gallery   
41                  Park            Pizza Place                   Bar   
51           Pizza Place  Vietnamese Restaurant           Coffee Shop   
52                   Bar     Mexican Restaurant                Bakery   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
26                Bakery            Hobby Shop    Italian Restaurant   
32   American Restaurant                Bakery   Filipino Restaurant   
34         Hot Dog Joint        Ice Cream Shop    Mexican Restaurant   
36           Coffee Shop        Ice Cream Shop           Pizza Place   
40                   Bar              Beer Bar           Coffee Shop   
41   American Restaurant    Seafood Restaurant    Italian Restaurant   
51    Chinese Restaurant                   Bar            Hobby Shop   
52          Cocktail Bar    Chinese Restaurant           Record Shop   

        7th Most Common Venue  8th Most Common Venue 9th Most Common Venue  \
26          Korean Restaurant     Chinese Restaurant      Greek Restaurant   
32                       Park     Chinese Restaurant            Bagel Shop   
34                Art Gallery  Vietnamese Restaurant          Burger Joint   
36  Middle Eastern Restaurant                   Park      Ramen Restaurant   
40          French Restaurant                   Park   American Restaurant   
41         Mexican Restaurant            Coffee Shop          Cocktail Bar   
51         Italian Restaurant            Flower Shop    Mexican Restaurant   
52                  Speakeasy    American Restaurant    Italian Restaurant   

   10th Most Common Venue  
26  Vietnamese Restaurant  
32           Dessert Shop  
34                 Bakery  
36   Caribbean Restaurant  
40              Speakeasy  
41           Burger Joint  
51    American Restaurant  
52            Art Gallery

In [171]:
address = 'Chicago, IL'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)


rainbow =  ['#8000ff', '#000080', '#10a2f0', '#2adddd', '#00ff00', '#fb8662', '#0b6623', '#ffa256', '#ff72be', '#ff0000']

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(city5_merged['Latitude'], city5_merged['Longitude'], city5_merged['Neighborhood'], city5_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [181]:
city5_merged[(city5_merged['Cluster Labels'] == 3) & (city5_merged['City'] == 'San Francisco')]

City           Neighborhood   Latitude   Longitude  \
111  San Francisco             Anza Vista  37.781004 -122.444436   
114  San Francisco         Bernal Heights  37.739540 -122.418049   
116  San Francisco         Cathedral Hill  37.784344 -122.426738   
117  San Francisco            China Basin  37.779502 -122.394993   
118  San Francisco              Chinatown  37.796596 -122.408582   
119  San Francisco           Civic Center  37.778972 -122.420653   
122  San Francisco        Design District  37.768924 -122.403910   
123  San Francisco        Dolores Heights  37.756947 -122.437816   
124  San Francisco        Duboce Triangle  37.766159 -122.435493   
126  San Francisco              Excelsior  37.724133 -122.438455   
128  San Francisco     Financial District  37.792773 -122.409847   
131  San Francisco         Haight Ashbury  37.769930 -122.446916   
132  San Francisco           Hayes Valley  37.774713 -122.429710   
133  San Francisco              Ingleside  37.722987 -122.453027   
136  San Francisco            Jordan Park  37.783794 -122.460746   
137  San Francisco               Lakeside  37.725884 -122.482213   
138  San Francisco         Laurel Heights  37.784418 -122.454827   
140  San Francisco          Little Russia  37.780238 -122.485924   
141  San Francisco          Lone Mountain  37.778345 -122.457045   
142  San Francisco           Lower Haight  37.771721 -122.438088   
143  San Francisco         Lower Nob Hill  37.789084 -122.418035   
144  San Francisco  Lower Pacific Heights  37.786292 -122.444531   
147  San Francisco             Mid Market  37.780153 -122.415837   
148  San Francisco            Mission Bay  37.771456 -122.399293   
149  San Francisco       Mission District  37.759930 -122.419138   
151  San Francisco         Mount Davidson  37.738332 -122.462088   
152  San Francisco               Nob Hill  37.792944 -122.420489   
154  San Francisco            North Beach  37.805762 -122.412193   
156  San Francisco        Pacific Heights  37.784929 -122.452194   
160  San Francisco      Richmond District  37.780485 -122.472472   
162  San Francisco           Russian Hill  37.800849 -122.424709   
164  San Francisco                   SoMa  37.780814 -122.419928   
165  San Francisco            South Beach  37.786367 -122.404228   
168  San Francisco             Tenderloin  37.783929 -122.421807   
169  San Francisco           Union Square  37.787933 -122.409687   
172  San Francisco       Western Addition  37.785207 -122.446916   

     Cluster Labels  1st Most Common Venue          2nd Most Common Venue  \
111               3               Wine Bar                    Coffee Shop   
114               3            Coffee Shop                    Pizza Place   
116               3              Gift Shop               Ramen Restaurant   
117               3            Coffee Shop                            Bar   
118               3     Chinese Restaurant             Italian Restaurant   
119               3           Cocktail Bar                    Coffee Shop   
122               3            Art Gallery            American Restaurant   
123               3            Coffee Shop                      Wine Shop   
124               3            Coffee Shop                           Park   
126               3                 Bakery             Mexican Restaurant   
128               3                 Bakery                    Coffee Shop   
131               3            Coffee Shop                      Gift Shop   
132               3                   Park                       Wine Bar   
133               3  Vietnamese Restaurant                    Coffee Shop   
136               3     Chinese Restaurant                         Bakery   
137               3              Juice Bar                    Pizza Place   
138               3    American Restaurant                    Coffee Shop   
140               3     Chinese Restaurant          Vietnamese Restaurant   
141               3            Piz

In [172]:
address = 'San Francisco, CA USA'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=13)


rainbow =  ['#8000ff', '#000080', '#10a2f0', '#2adddd', '#00ff00', '#fb8662', '#0b6623', '#ffa256', '#ff72be', '#ff0000']

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(city5_merged['Latitude'], city5_merged['Longitude'], city5_merged['Neighborhood'], city5_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [184]:
city5_merged[(city5_merged['Cluster Labels'] == 3) & (city5_merged['City'] == 'Portland OR')]

City        Neighborhood   Latitude   Longitude  Cluster Labels  \
77   Portland OR               Boise  45.549109 -122.678953               3   
83   Portland OR           Hillsdale  45.481507 -122.694818               3   
91   Portland OR          Montavilla  45.519008 -122.578982               3   
92   Portland OR           Mt. Tabor  45.514292 -122.616607               3   
94   Portland OR  Old Town Chinatown  45.525317 -122.681385               3   
95   Portland OR      Pearl District  45.530447 -122.689350               3   
96   Portland OR   Portland Downtown  45.523452 -122.676207               3   
99   Portland OR            Richmond  45.504440 -122.631318               3   
100  Portland OR      Rose City Park  45.537814 -122.623149               3   
102  Portland OR               Sabin  45.552989 -122.657579               3   
103  Portland OR   Sellwood Moreland  45.464564 -122.652595               3   
104  Portland OR     Sullivans Gulch  45.531934 -122.651367               3   
109  Portland OR           Woodstock  45.479008 -122.608427               3   

    1st Most Common Venue  2nd Most Common Venue 3rd Most Common Venue  \
77            Pizza Place                    Bar    Mexican Restaurant   
83            Pizza Place     Mexican Restaurant    Chinese Restaurant   
91            Coffee Shop  Vietnamese Restaurant                   Bar   
92            Coffee Shop                    Bar           Pizza Place   
94            Coffee Shop            Pizza Place   American Restaurant   
95            Coffee Shop     Italian Restaurant                   Bar   
96            Coffee Shop    American Restaurant          Cocktail Bar   
99         Ice Cream Shop            Pizza Place              Wine Bar   
100    Chinese Restaurant            Coffee Shop   American Restaurant   
102                Bakery              Speakeasy                   Spa   
103    Italian Restaurant            Pizza Place           Coffee Shop   
104   American Restaurant                    Spa           Coffee Shop   
109           Pizza Place     Mexican Restaurant                   Bar   

             4th Most Common Venue          5th Most Common Venue  \
77   Vegetarian / Vegan Restaurant                      Gift Shop   
83                  Ice Cream Shop             Italian Restaurant   
91                    Cupcake Shop                   Dessert Shop   
92           Vietnamese Restaurant  Vegetarian / Vegan Restaurant   
94                  Ice Cream Shop                   Cocktail Bar   
95                    Cocktail Bar                            Spa   
96              Mexican Restaurant                   Burger Joint   
99             Arts & Crafts Store             Italian Restaurant   
100                       Wine Bar                 Ice Cream Shop   
102                 Farmers Market             Mexican Restaurant   
103          Vietnamese Restaurant                 Ice Cream Shop   
104                   Cocktail Bar             Italian Restaurant   
109  Vegetarian / Vegan Restaurant              French Restaurant   

             6th Most Common Venue 7th Most Common Venue  \
77             American Restaurant           Coffee Shop   
83                  Farmers Market           Coffee Shop   
91       Middle Eastern Restaurant        Farmers Market   
92                       Wine Shop                Bakery   
94              Mexican Restaurant                   Bar   
95                       Wine Shop           Pizza Place   
96   Vegetarian / Vegan Restaurant           Pizza Place   
99                          Bakery          Burger Joint   
100            Japanese Restaurant     Korean Restaurant   
102                      Wine Shop          Cocktail Bar   
103                  Garden Center          Cupcake Shop   
104            Japanese Restaurant             Juice Bar   
109                   Burger Joint              Beer Bar   

    8th Most Common Venue 9th Most Common Venue 10th Most Co

In [183]:
address = 'Portland, OR'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)


rainbow =  ['#8000ff', '#000080', '#10a2f0', '#2adddd', '#00ff00', '#fb8662', '#0b6623', '#ffa256', '#ff72be', '#ff0000']

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(city5_merged['Latitude'], city5_merged['Longitude'], city5_merged['Neighborhood'], city5_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [193]:
EastVillageCluster = city5_merged[city5_merged['Cluster Labels'] == 3]
print(EastVillageCluster.shape)
EastVillageCluster.head()

(70, 15)


City Neighborhood   Latitude  Longitude  Cluster Labels  \
1   Boston     Back Bay  42.350097 -71.086996               3   
2   Boston  Bay Village  42.350653 -71.069773               3   
6   Boston    Chinatown  42.349814 -71.068382               3   
7   Boston     Downtown  42.354542 -71.057829               3   
14  Boston    South End  42.339443 -71.084551               3   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
1    American Restaurant        Ice Cream Shop    Italian Restaurant   
2                    Spa   American Restaurant    Seafood Restaurant   
6    American Restaurant                   Spa    Italian Restaurant   
7            Coffee Shop                  Park                Bakery   
14                Bakery           Coffee Shop   American Restaurant   

   4th Most Common Venue      5th Most Common Venue  6th Most Common Venue  \
1                    Bar                Coffee Shop  Vietnamese Restaurant   
2     Italian Restaurant                       Park                 Bakery   
6     Seafood Restaurant                Pizza Place                 Bakery   
7     Italian Restaurant        American Restaurant           Burger Joint   
14    Italian Restaurant  Middle Eastern Restaurant            Pizza Place   

   7th Most Common Venue 8th Most Common Venue  9th Most Common Venue  \
1           Burger Joint    Seafood Restaurant     Mexican Restaurant   
2            Coffee Shop     French Restaurant     Mexican Restaurant   
6      French Restaurant    Mexican Restaurant                   Park   
7     Chinese Restaurant              Wine Bar           Cocktail Bar   
14   Arts & Crafts Store          Burger Joint  Vietnamese Restaurant   

   10th Most Common Venue  
1                  Bakery  
2     Arts & Crafts Store  
6     Arts & Crafts Store  
7          Farmers Market  
14     Chinese Restaurant

## Results - Review Maps of each city with only cluster 3 locations.

In [187]:
address = 'Philadelphia, PA'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map of Philadelphia using latitude and longitude values
map_city = folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map
for lat, lng, neighborhood in zip(EastVillageCluster['Latitude'], EastVillageCluster['Longitude'],  EastVillageCluster['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_city)  
    
map_city

In [189]:
address = 'Boston, MA'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map of Philadelphia using latitude and longitude values
map_city = folium.Map(location=[latitude, longitude], zoom_start=13)

# add markers to map
for lat, lng, neighborhood in zip(EastVillageCluster['Latitude'], EastVillageCluster['Longitude'],  EastVillageCluster['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_city)  
    
map_city

In [190]:
address = 'Chicago, IL'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map of Philadelphia using latitude and longitude values
map_city = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(EastVillageCluster['Latitude'], EastVillageCluster['Longitude'],  EastVillageCluster['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_city)  
    
map_city

In [191]:
address = 'San Francisco, CA USA'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map of Philadelphia using latitude and longitude values
map_city = folium.Map(location=[latitude, longitude], zoom_start=13)

# add markers to map
for lat, lng, neighborhood in zip(EastVillageCluster['Latitude'], EastVillageCluster['Longitude'],  EastVillageCluster['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_city)  
    
map_city

In [192]:
address = 'Portland, OR'

geolocator = Nominatim(user_agent="us_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map of Philadelphia using latitude and longitude values
map_city = folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map
for lat, lng, neighborhood in zip(EastVillageCluster['Latitude'], EastVillageCluster['Longitude'],  EastVillageCluster['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_city)  
    
map_city

## Conclusions
### Within the 5 cities on the top 10 public transportation list (San Francisco, Boston, Philadelphia, Chicago and Portland, OR), the method was able to analyze 8,583 venues to predict neighborhoods that are like the East Village in New York City. The process came back with 70 neighborhoods for my friend to consider.

## Future Considerations
### Although 57 venue categories were used, data used from FourSquare might not have translated between the 5 cities since many venue categories were excluded.  More data would have been helpful such as age, rent/home costs, and median income.  This data was not available, for free, at the granularity that was required.  Looking at preference data from FourSquare also could have made a stronger model.
